In [53]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import xgboost as xgb
import lightgbm as lgb
import statsmodels.api as sm
import warnings
import shap
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_validate
from sklearn.ensemble import VotingClassifier
from sklearn.ensemble import VotingRegressor
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import RobustScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import StratifiedKFold
from pycaret.regression import *
from xgboost import XGBRegressor
from xgboost import XGBClassifier
from sklearn.tree import ExtraTreeClassifier
from sklearn.tree import ExtraTreeRegressor
from sklearn.experimental import enable_iterative_imputer 
from sklearn.impute import KNNImputer
from sklearn.impute import IterativeImputer
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import RandomForestRegressor
from catboost import CatBoostClassifier, Pool
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import AdaBoostRegressor
from catboost import CatBoostRegressor
from catboost import CatBoostClassifier
from sklearn.metrics import mean_squared_error
from sklearn.impute import KNNImputer

In [2]:
warnings.simplefilter(action='ignore')
pd.set_option('display.max_columns', None)

In [3]:
train_data = pd.read_csv("./train.csv")

In [196]:
train_data.describe()

Y_Class   Y_Quality         X_1         X_2    X_3    X_4  \
count  598.000000  598.000000  349.000000  349.000000  349.0  349.0   
mean     1.025084    0.530896    2.409742   95.123209    0.0   45.0   
std      0.565069    0.007401    5.895256    4.107640    0.0    0.0   
min      0.000000    0.500856    1.000000   87.000000    0.0   45.0   
25%      1.000000    0.527535    2.000000   93.000000    0.0   45.0   
50%      1.000000    0.530436    2.000000   95.000000    0.0   45.0   
75%      1.000000    0.533433    2.000000   98.000000    0.0   45.0   
max      2.000000    0.578841  103.000000  102.000000    0.0   45.0   

              X_5    X_6         X_7         X_8  ...      X_2863      X_2864  \
count  349.000000  349.0  349.000000  349.000000  ...  249.000000  249.000000   
mean    10.392550    0.0   48.802292   10.048711  ...  423.558233  406.088187   
std      0.489019    0.0    4.373824    0.215571  ...   38.335184   37.299901   
min     10.000000    0.0   45.000000   10.000000  ...  373.000000  357.698113   
25%     10.000000    0.0   45.000000   10.000000  ...  384.000000  368.296296   
50%     10.000000    0.0   45.000000   10.000000  ...  446.000000  427.867925   
75%     11.000000    0.0   51.000000   10.000000  ...  465.000000  443.807692   
max     11.000000    0.0   62.000000   11.000000  ...  473.000000  450.692308   

           X_2865      X_2866     X_2867      X_2868      X_2869     X_2870  \
count  249.000000  100.000000  100.00000  100.000000  100.000000  100.00000   
mean   388.064257   50.807300   53.60770   49.606200   51.659800   66.64970   
std     36.054561    7.011828    8.13899    7.158917    8.913065    4.52781   
min    342.000000   32.120000   31.70000   32.560000   30.490000   61.67000   
25%    352.000000   49.485000   52.20000   42.160000   49.915000   63.64500   
50%    406.000000   53.425000   55.92500   51.460000   56.175000   65.14000   
75%    423.000000   55.287500   58.97500   55.030000   57.175000   67.11500   
max    434.000000   60.240000   68.66000   60.410000   59.930000   79.75000   

       X_2871        HOUR  
count    99.0  598.000000  
mean      1.0   10.688963  
std       0.0    6.607461  
min       1.0    0.000000  
25%       1.0    5.250000  
50%       1.0   10.000000  
75%       1.0   16.000000  
max       1.0   23.000000  

[8 rows x 2796 columns]

In [4]:
train_data['YEAR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.year
train_data['MONTH'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.month
train_data['DAY'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day
train_data['HOUR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.hour
train_data['MINUTE'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.minute
train_data['DAY_OF_WEEK'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day_name()

In [5]:
train_data = train_data.drop(['MONTH', 'DAY', 'YEAR', 'MINUTE'], axis = 1)

In [6]:
colls = []
for coll in train_data :
    if 'X' in coll and train_data[coll].isna().sum() == 598 :
        colls.append(coll)
print(len(colls))

82


In [7]:
train_data.drop(colls, inplace = True, axis = 1)

In [8]:
train_data.loc[train_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
train_data.loc[train_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
train_data.loc[train_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

train_data.loc[train_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
train_data.loc[train_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
train_data.loc[train_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
train_data.loc[train_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
train_data.loc[train_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
train_data.loc[train_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
train_data.loc[train_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

train_data.drop(['PRODUCT_ID', 'TIMESTAMP', 'PRODUCT_CODE'], axis = 1, inplace = True)
train_data

Y_Class  Y_Quality     LINE   X_1   X_2  X_3   X_4   X_5  X_6   X_7  \
0          1   0.533433  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
1          2   0.541819  T050307   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
2          1   0.531267  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
3          2   0.537325  T050307   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
4          1   0.531590  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
..       ...        ...      ...   ...   ...  ...   ...   ...  ...   ...   
593        1   0.526546  T100306   2.0  95.0  0.0  45.0  10.0  0.0  50.0   
594        0   0.524022  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
595        0   0.521289  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
596        1   0.531375  T100304  40.0  94.0  0.0  45.0  11.0  0.0  45.0   
597        1   0.533702  T100306  21.0  87.0  0.0  45.0  10.0  0.0  61.0   

      X_8   X_9  X_10   X_11   X_12   X_13  X_14  X_15   X_16   X_17   X_18  \
0     NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN    NaN   
1     NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN    NaN   
2     NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN    NaN   
3     NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN    NaN   
4     NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN    NaN   
..    ...   ...   ...    ...    ...    ...   ...   ...    ...    ...    ...   
593  10.0  52.0   2.0  468.9  473.9  459.2   0.0   0.0  247.5  248.0  247.3   
594   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN    NaN   
595   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN    NaN   
596  10.0  31.0   2.0  505.8  510.9  497.1   0.0   0.0  247.5  248.1  247.3   
597  10.0  52.0   2.0  470.6  474.9  462.9   0.0   0.0  247.5  248.0  247.3   

      X_19   X_20   X_21   X_22  X_23  X_24  X_25   X_26   X_27   X_28   X_29  \
0      NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN    NaN   
1      NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN    NaN   
2      NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN    NaN   
3      NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN    NaN   
4      NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN    NaN   
..     ...    ...    ...    ...   ...   ...   ...    ...    ...    ...    ...   
593  250.0  527.0  538.0  522.0  0.19  0.19  0.19  155.0  155.0  155.0  155.0   
594    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN    NaN   
595    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN    NaN   
596  250.0  489.0  498.0  485.0  0.19  0.19  0.19  155.0  155.0  155.0  155.0   
597  250.0  525.0  534.0  520.0  0.19  0.20  0.19  155.0  155.0  155.0  155.0   

      X_30   X_31   X_32   X_33   X_34   X_35   X_36   X_37   X_38  X_39  \
0      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
1      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
2      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
3      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
4      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...   ...   
593  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0  0.075   2.0   
594    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
595    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
596  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0  0.078   1.0   
597  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0  0.077   1.0   

     X_40  X_41  X_42  X_43  X_44  X_45  X_46  X_47  X_48  X_49  X_50  X_51  \
0     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
1     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2     NaN   NaN   Na

In [9]:
T050304 = train_data[train_data['LINE'] == 'T050304']
T050307 = train_data[train_data['LINE'] == 'T050307']
T010305 = train_data[train_data['LINE'] == 'T010305']
T010306 = train_data[train_data['LINE'] == 'T010306']
T100304 = train_data[train_data['LINE'] == 'T100304']
T100306 = train_data[train_data['LINE'] == 'T100306']

In [10]:
T050304.drop(['LINE'], axis = 1, inplace = True)
T050307.drop(['LINE'], axis = 1, inplace = True)
T010305.drop(['LINE'], axis = 1, inplace = True)
T010306.drop(['LINE'], axis = 1, inplace = True)
T100304.drop(['LINE'], axis = 1, inplace = True)
T100306.drop(['LINE'], axis = 1, inplace = True)

In [11]:
T050304_col = []
for col in T050304 :
    if 'X' in col and T050304[col].isna().sum() == len(T050304) :
        T050304_col.append(col)
print(len(T050304_col))

T050304.drop(T050304_col, inplace = True, axis = 1)

825


In [17]:
T050307_col = []
for col in T050307 :
    if 'X' in col and T050307[col].isna().sum() == len(T050307) :
        T050307_col.append(col)
print(len(T050307_col))

T050307.drop(T050307_col, inplace = True, axis = 1)

818


In [12]:
T010305_col = []
for col in T010305 :
    if 'X' in col and T010305[col].isna().sum() == len(T010305) :
        T010305_col.append(col)
print(len(T010305_col))

T010305.drop(T010305_col, inplace = True, axis = 1)

1907


In [13]:
T010306_col = []
for col in T010306 :
    if 'X' in col and T010306[col].isna().sum() == len(T010306) :
        T010306_col.append(col)
print(len(T010306_col))

T010306.drop(T010306_col, inplace = True, axis = 1)

1907


In [14]:
T100304_col = []
for col in T100304 :
    if 'X' in col and T100304[col].isna().sum() == len(T100304) :
        T100304_col.append(col)
print(len(T100304_col))

T100304.drop(T100304_col, inplace = True, axis = 1)

2122


In [15]:
T100306_col = []
for col in T100306 :
    if 'X' in col and T100306[col].isna().sum() == len(T100306) :
        T100306_col.append(col)
print(len(T100306_col))

T100306.drop(T100306_col, inplace = True, axis = 1)

2122


In [18]:
T051 = list(set(T050307_col)-set(T050304_col))
T052 = list(set(T050304_col)-set(T050307_col))
T5drop = T051 + T052

T011 = list(set(T010305_col)-set(T010306_col))
T012 = list(set(T010306_col)-set(T010305_col))
T0drop = T011 + T012

T101 = list(set(T100304_col)-set(T100306_col))
T102 = list(set(T100306_col)-set(T100304_col))
T1drop = T101 + T102

In [19]:
T05 = pd.concat([T050304, T050307])
T01 = pd.concat([T010305, T010306])
T10 = pd.concat([T100304, T100306])

In [20]:
T05.drop(T5drop, inplace = True, axis = 1)
T01.drop(T0drop, inplace = True, axis = 1)
T10.drop(T1drop, inplace = True, axis = 1)

In [23]:
T050 = T05[T05['Y_Class'] == 0]
T051 = T05[T05['Y_Class'] == 1]
T052 = T05[T05['Y_Class'] == 2]

T010 = T01[T01['Y_Class'] == 0]
T011 = T01[T01['Y_Class'] == 1]
T012 = T01[T01['Y_Class'] == 2]

T100 = T10[T10['Y_Class'] == 0]
T101 = T10[T10['Y_Class'] == 1]
T102 = T10[T10['Y_Class'] == 2]

T050 = T050.fillna(T050.mean())
T051 = T051.fillna(T051.mean())
T052 = T052.fillna(T052.mean())

T010 = T010.fillna(T010.mean())
T011 = T011.fillna(T011.mean())
T012 = T012.fillna(T012.mean())

T100 = T100.fillna(T100.mean())
T101 = T101.fillna(T101.mean())
T102 = T102.fillna(T102.mean())

T05 = pd.concat([T050, T051, T052])
T01 = pd.concat([T010, T011, T012])
T10 = pd.concat([T100, T101, T102])

In [55]:
T05_class = T05['Y_Class']
T05_target = T05['Y_Quality']
T05_data = T05.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [56]:
T_05c = T05_data.columns
T_05scaler = RobustScaler()
T_05scaled = T_05scaler.fit_transform(T05_data)
T05_data = pd.DataFrame(T_05scaled, columns = T_05c)
T05_data

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
0     -1.0    0.0   -1.0    0.0  0.211968  0.209939  0.206826  0.498623   
1      0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709 -0.663912   
2      0.0    0.0   -1.0    0.0 -0.412779 -0.414807 -0.416709 -0.713499   
3      0.0    0.0    0.0    0.0 -0.410751 -0.412779 -0.414671 -0.856749   
4     -1.0    0.0   -1.0    0.0 -0.256592 -0.258621 -0.259806 -0.426997   
..     ...    ...    ...    ...       ...       ...       ...       ...   
115   -1.0    0.0   -1.0    0.0  0.917850  0.915822  0.920020  0.438017   
116    0.0    0.0    0.0    0.0 -0.526369 -0.524341 -0.526745 -1.005510   
117    0.0    0.0    0.0    0.0 -0.343813 -0.341785 -0.343352 -0.719008   
118    0.0    0.0    0.0    0.0 -0.343813 -0.341785 -0.343352 -0.724518   
119    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560 -0.873278   

        X_140     X_141  X_142  X_143  X_144  X_145     X_146  X_147  \
0    0.414966  0.752604    0.0    0.0    0.0    0.0  0.438687    0.0   
1   -0.632653 -0.330729    0.0    0.0    0.0    0.0  0.583765    0.0   
2   -0.664399 -0.440104    0.0    0.0    0.0    0.0  0.511226    0.0   
3   -0.773243 -0.617187    0.0    0.0    0.0    0.0  0.535406    0.0   
4   -0.392290 -0.221354    0.0    0.0   -1.0    0.0  0.183074    0.0   
..        ...       ...    ...    ...    ...    ...       ...    ...   
115  0.414966  0.268229    0.0    0.0   -1.0    0.0 -0.673575    0.0   
116 -0.895692 -0.658854    0.0    0.0    0.0    0.0  0.597582    0.0   
117 -0.623583 -0.351562    0.0    0.0    0.0    0.0  0.528497    0.0   
118 -0.628118 -0.752604    0.0    0.0   -2.0    0.0 -0.635579    0.0   
119 -0.746032 -0.700521    0.0    0.0   -1.0    0.0  0.231434    0.0   

        X_148     X_149   X_150  X_151  X_152  X_153  X_154  X_155  X_156  \
0   -0.518519 -0.436364 -0.4375    0.0    0.1    0.0    0.0    0.0    0.1   
1    0.666667  0.654545  0.6250    0.0    0.1    0.0    0.0    0.0    0.0   
2    0.666667  0.727273  0.6875    0.0    0.0    0.0    0.0    0.0    0.0   
3    0.888889  0.945455  0.7500    0.0    0.0    0.0    0.0    0.0    0.0   
4    0.370370  0.363636  0.3750   -1.0    0.0    0.0    0.0   -1.0    0.0   
..        ...       ...     ...    ...    ...    ...    ...    ...    ...   
115 -0.444444 -0.363636 -0.4375    0.0    0.0    0.0    0.0    0.0    0.0   
116  1.037037  1.018182  0.9375    0.0    0.0   -1.0    0.0   -1.0    0.0   
117  0.740741  0.727273  0.6250    0.0    0.0    0.0    0.0    0.0    0.0   
118  0.740741  0.727273  0.6250    0.0   -0.1   -1.0    0.0    0.0    0.0   
119  0.888889  0.945455  0.7500   -1.0    0.0   -1.0    0.0   -1.0    0.0   

     X_157  X_158  X_159  X_160  X_161  X_162  X_163  X_164  X_165  X_166  \
0      0.1    0.0   -1.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
1      0.0    0.0    0.0    0.1    0.1    0.0   -0.1    0.0   -0.5    0.0   
2      0.0    0.0    0.0    0.1    0.1    0.0   -0.1    0.0   -0.5    0.0   
3      0.0    0.0   -1.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
4      0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
115    0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
116    0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
117    0.0    0.0    0.0    0.0    0.0    0.0   -0.1    0.0   -0.5    0.0   
118    0.0    0.0    0.0    0.1    0.0    0.0    0.0    0.0   -0.5    0.0   
119   -0.1    0.0    0.0    0.1    0.0    0.0    0.0    0.0    0.5    0.0   

     X_167  X_168  X_169  X_170  X_171  X_172  X_173  X_174  X_175  X_176  \
0      0.0    0.0    0.0    0.0   -1.0    0.0    0.0    0.0    0.0    0.0   
1      0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.1   
2      0.0   -0.1   -0.1    0.0    0.0    0.0    0.0    0.0    1.0    0.0   
3     -1.0    0.1   -0.1    0.0   -1.0    0.0    0.0    0.0    0.0    0.0   
4   

In [57]:
T05_y_class = pd.DataFrame(T05_target, columns = ['Y_Quality'])
T05_idx = T05_y_class.index
T05_y_class = T05_y_class.reset_index()
T05_data = pd.concat([T05_data, T05_y_class], axis = 1)
T05_data = T05_data.set_index('index')
T05_data.drop(['Y_Quality'], axis = 1, inplace = True)
T05_data

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
index                                                                       
34      -1.0    0.0   -1.0    0.0  0.211968  0.209939  0.206826  0.498623   
109      0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709 -0.663912   
110      0.0    0.0   -1.0    0.0 -0.412779 -0.414807 -0.416709 -0.713499   
111      0.0    0.0    0.0    0.0 -0.410751 -0.412779 -0.414671 -0.856749   
131     -1.0    0.0   -1.0    0.0 -0.256592 -0.258621 -0.259806 -0.426997   
...      ...    ...    ...    ...       ...       ...       ...       ...   
261     -1.0    0.0   -1.0    0.0  0.917850  0.915822  0.920020  0.438017   
316      0.0    0.0    0.0    0.0 -0.526369 -0.524341 -0.526745 -1.005510   
355      0.0    0.0    0.0    0.0 -0.343813 -0.341785 -0.343352 -0.719008   
356      0.0    0.0    0.0    0.0 -0.343813 -0.341785 -0.343352 -0.724518   
369      0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560 -0.873278   

          X_140     X_141  X_142  X_143  X_144  X_145     X_146  X_147  \
index                                                                    
34     0.414966  0.752604    0.0    0.0    0.0    0.0  0.438687    0.0   
109   -0.632653 -0.330729    0.0    0.0    0.0    0.0  0.583765    0.0   
110   -0.664399 -0.440104    0.0    0.0    0.0    0.0  0.511226    0.0   
111   -0.773243 -0.617187    0.0    0.0    0.0    0.0  0.535406    0.0   
131   -0.392290 -0.221354    0.0    0.0   -1.0    0.0  0.183074    0.0   
...         ...       ...    ...    ...    ...    ...       ...    ...   
261    0.414966  0.268229    0.0    0.0   -1.0    0.0 -0.673575    0.0   
316   -0.895692 -0.658854    0.0    0.0    0.0    0.0  0.597582    0.0   
355   -0.623583 -0.351562    0.0    0.0    0.0    0.0  0.528497    0.0   
356   -0.628118 -0.752604    0.0    0.0   -2.0    0.0 -0.635579    0.0   
369   -0.746032 -0.700521    0.0    0.0   -1.0    0.0  0.231434    0.0   

          X_148     X_149   X_150  X_151  X_152  X_153  X_154  X_155  X_156  \
index                                                                         
34    -0.518519 -0.436364 -0.4375    0.0    0.1    0.0    0.0    0.0    0.1   
109    0.666667  0.654545  0.6250    0.0    0.1    0.0    0.0    0.0    0.0   
110    0.666667  0.727273  0.6875    0.0    0.0    0.0    0.0    0.0    0.0   
111    0.888889  0.945455  0.7500    0.0    0.0    0.0    0.0    0.0    0.0   
131    0.370370  0.363636  0.3750   -1.0    0.0    0.0    0.0   -1.0    0.0   
...         ...       ...     ...    ...    ...    ...    ...    ...    ...   
261   -0.444444 -0.363636 -0.4375    0.0    0.0    0.0    0.0    0.0    0.0   
316    1.037037  1.018182  0.9375    0.0    0.0   -1.0    0.0   -1.0    0.0   
355    0.740741  0.727273  0.6250    0.0    0.0    0.0    0.0    0.0    0.0   
356    0.740741  0.727273  0.6250    0.0   -0.1   -1.0    0.0    0.0    0.0   
369    0.888889  0.945455  0.7500   -1.0    0.0   -1.0    0.0   -1.0    0.0   

       X_157  X_158  X_159  X_160  X_161  X_162  X_163  X_164  X_165  X_166  \
index                                                                         
34       0.1    0.0   -1.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
109      0.0    0.0    0.0    0.1    0.1    0.0   -0.1    0.0   -0.5    0.0   
110      0.0    0.0    0.0    0.1    0.1    0.0   -0.1    0.0   -0.5    0.0   
111      0.0    0.0   -1.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
131      0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
...      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
261      0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
316      0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
355      0.0    0.0    0.0    0.0    0.0    0.0   -0.1    0.0   -0.5    0.0   
356      0.0    0.0    0.0    0.1    0.0    0.0    0.0    0.0   -0.5    0.0   
369     -0.1    0.0    0.0    0.1    0.0    0.0    0.0    0.0    0

In [59]:
#13
setup_rgs = setup(data = T05_data, target = T05_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [60]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbr = create_model('gbr', fold = 5)
T05_total_models.append(T05_model_gbr)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [61]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbr = tune_model(T05_model_gbr, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [62]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbr, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]
T05_tuned_models

[LGBMRegressor(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
               importance_type='split', learning_rate=0.1, max_depth=-1,
               min_child_samples=20, min_child_weight=0.001, min_split_gain=0.0,
               n_estimators=100, n_jobs=-1, num_leaves=31, objective=None,
               random_state=414, reg_alpha=0.0, reg_lambda=0.0, silent=True,
               subsample=1.0, subsample_for_bin=200000, subsample_freq=0),
 RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='squared_error',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       max_samples=None, min_impurity_decrease=0.0,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=-1,
                       oob_score=False, random_state=414, verbose=0,
                       warm_start=False),
 GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0, c

In [63]:
for model in T05_tuned_models:
    display(predict_model(model))

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     0.0    0.0    0.0    0.0  0.662272  0.660243  0.657157  1.330579   
85    -1.0   -1.0   -1.0    0.0 -0.597363 -0.599391 -0.602140 -1.011019   
86     0.0    0.0    0.0    0.0  1.017241  1.015213  1.019868  0.707989   
87     0.0    0.0    0.0    0.0  0.879310  0.877282  0.881304  0.366391   
88    -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.008264   
89    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.008264   
90    -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.628099   
91    -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886  0.300275   
92     0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388  0.190083   
93    -1.0    0.0   -1.0    0.0 -0.544625 -0.546653 -0.549159 -1.710744   
94     0.0   -1.0    0.0    0.0  0.996957  0.994929  0.999491  0.785124   
95     0.0    0.0    0.0    0.0 -0.560852 -0.558824 -0.561386 -1.214876   
96     0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709 -0.663912   
97     0.0    0.0    0.0    0.0  0.899594  0.897566  0.901681  0.680441   
98     0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654  0.371901   
99     0.0    0.0    0.0    0.0  0.406694  0.404665  0.400408  0.702479   
100    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261  0.327824   
101   -2.0   -1.0   -2.0    0.0 -0.195740 -0.197769 -0.198675 -0.002755   
102    0.0    0.0    0.0    0.0  0.175456  0.175456  0.176261  0.327824   
103    0.0    0.0    0.0    0.0 -0.526369 -0.524341 -0.526745 -1.005510   
104    0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639  1.071625   
105    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560 -0.873278   
106   -1.0    0.0   -1.0    0.0 -0.538540 -0.538540 -0.541009 -0.730028   
107   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
108   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.035813   
109    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683  0.641873   
110    0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042  0.520661   
111    0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007 -0.079890   
112    0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656 -0.184573   
113   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751  0.019284   
114    0.0    0.0   -1.0    0.0  0.662272  0.660243  0.657157  1.325069   
115    0.0    0.0    0.0    0.0  1.007099  1.005071  1.009679  0.933884   
116    0.0    0.0    0.0    0.0  0.905680  0.903651  0.907794  0.768595   
117   -1.0   -1.0   -1.0    0.0 -0.272819 -0.274848 -0.276108 -0.157025   
118   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.024793   
119   -1.0   -1.0   -1.0    0.0 -0.597363 -0.599391 -0.602140 -1.033058   

        X_140     X_141  ...    X_2866    X_2867    X_2868    X_2869  \
84   1.195011  1.216146  ...  0.064262  0.000000  0.785106  0.304313   
85  -0.868481 -0.903646  ... -0.324895  0.236102  0.201773  0.064288   
86   0.664399  0.908854  ... -0.419956  0.571858 -0.847891 -0.319507   
87   0.342404  0.278646  ...  0.567790  0.921412 -0.816746 -0.348748   
88   0.002268 -0.570312  ... -0.200127  0.620918  0.331402  0.166634   
89  -0.052154  0.054688  ... -3.109893 -3.196578  0.358338 -2.744118   
90  -1.340136 -2.565104  ...  0.016732 -0.363352 -0.050753  0.176381   
91   0.287982  0.205729  ...  0.000000  0.069487  0.000000  0.000000   
92   0.192744  0.039062  ...  0.454905  0.844755 -0.038126 -0.018563   
93  -1.408163 -1.533854  ...  0.046438  0.418545 -0.132402 -0.291484   
94   0.736961  0.252604  ... -0.691772  0.784963  0.207665 -0.766659   
95  -1.058957 -1.471354  ...  0.025644  1.151381  0.819618  0.396911   
96  -0.632653 -0.330729  ...  0.564819 -0.786496 -0.857150  0.201967   
97   0.637188  0.304688  ...  0.255870  0.903014  0.424837 -0.794682   
98   0.551020 -0.690104  ...  0.493524  2.003802  0.717766  0.455394   
99   0.637188  0.835938  ...  0.697014  1.516266  0.134433  0.104496   
100  

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     0.0    0.0    0.0    0.0  0.662272  0.660243  0.657157  1.330579   
85    -1.0   -1.0   -1.0    0.0 -0.597363 -0.599391 -0.602140 -1.011019   
86     0.0    0.0    0.0    0.0  1.017241  1.015213  1.019868  0.707989   
87     0.0    0.0    0.0    0.0  0.879310  0.877282  0.881304  0.366391   
88    -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.008264   
89    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.008264   
90    -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.628099   
91    -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886  0.300275   
92     0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388  0.190083   
93    -1.0    0.0   -1.0    0.0 -0.544625 -0.546653 -0.549159 -1.710744   
94     0.0   -1.0    0.0    0.0  0.996957  0.994929  0.999491  0.785124   
95     0.0    0.0    0.0    0.0 -0.560852 -0.558824 -0.561386 -1.214876   
96     0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709 -0.663912   
97     0.0    0.0    0.0    0.0  0.899594  0.897566  0.901681  0.680441   
98     0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654  0.371901   
99     0.0    0.0    0.0    0.0  0.406694  0.404665  0.400408  0.702479   
100    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261  0.327824   
101   -2.0   -1.0   -2.0    0.0 -0.195740 -0.197769 -0.198675 -0.002755   
102    0.0    0.0    0.0    0.0  0.175456  0.175456  0.176261  0.327824   
103    0.0    0.0    0.0    0.0 -0.526369 -0.524341 -0.526745 -1.005510   
104    0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639  1.071625   
105    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560 -0.873278   
106   -1.0    0.0   -1.0    0.0 -0.538540 -0.538540 -0.541009 -0.730028   
107   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
108   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.035813   
109    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683  0.641873   
110    0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042  0.520661   
111    0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007 -0.079890   
112    0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656 -0.184573   
113   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751  0.019284   
114    0.0    0.0   -1.0    0.0  0.662272  0.660243  0.657157  1.325069   
115    0.0    0.0    0.0    0.0  1.007099  1.005071  1.009679  0.933884   
116    0.0    0.0    0.0    0.0  0.905680  0.903651  0.907794  0.768595   
117   -1.0   -1.0   -1.0    0.0 -0.272819 -0.274848 -0.276108 -0.157025   
118   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.024793   
119   -1.0   -1.0   -1.0    0.0 -0.597363 -0.599391 -0.602140 -1.033058   

        X_140     X_141  ...    X_2866    X_2867    X_2868    X_2869  \
84   1.195011  1.216146  ...  0.064262  0.000000  0.785106  0.304313   
85  -0.868481 -0.903646  ... -0.324895  0.236102  0.201773  0.064288   
86   0.664399  0.908854  ... -0.419956  0.571858 -0.847891 -0.319507   
87   0.342404  0.278646  ...  0.567790  0.921412 -0.816746 -0.348748   
88   0.002268 -0.570312  ... -0.200127  0.620918  0.331402  0.166634   
89  -0.052154  0.054688  ... -3.109893 -3.196578  0.358338 -2.744118   
90  -1.340136 -2.565104  ...  0.016732 -0.363352 -0.050753  0.176381   
91   0.287982  0.205729  ...  0.000000  0.069487  0.000000  0.000000   
92   0.192744  0.039062  ...  0.454905  0.844755 -0.038126 -0.018563   
93  -1.408163 -1.533854  ...  0.046438  0.418545 -0.132402 -0.291484   
94   0.736961  0.252604  ... -0.691772  0.784963  0.207665 -0.766659   
95  -1.058957 -1.471354  ...  0.025644  1.151381  0.819618  0.396911   
96  -0.632653 -0.330729  ...  0.564819 -0.786496 -0.857150  0.201967   
97   0.637188  0.304688  ...  0.255870  0.903014  0.424837 -0.794682   
98   0.551020 -0.690104  ...  0.493524  2.003802  0.717766  0.455394   
99   0.637188  0.835938  ...  0.697014  1.516266  0.134433  0.104496   
100  

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     0.0    0.0    0.0    0.0  0.662272  0.660243  0.657157  1.330579   
85    -1.0   -1.0   -1.0    0.0 -0.597363 -0.599391 -0.602140 -1.011019   
86     0.0    0.0    0.0    0.0  1.017241  1.015213  1.019868  0.707989   
87     0.0    0.0    0.0    0.0  0.879310  0.877282  0.881304  0.366391   
88    -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.008264   
89    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.008264   
90    -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.628099   
91    -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886  0.300275   
92     0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388  0.190083   
93    -1.0    0.0   -1.0    0.0 -0.544625 -0.546653 -0.549159 -1.710744   
94     0.0   -1.0    0.0    0.0  0.996957  0.994929  0.999491  0.785124   
95     0.0    0.0    0.0    0.0 -0.560852 -0.558824 -0.561386 -1.214876   
96     0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709 -0.663912   
97     0.0    0.0    0.0    0.0  0.899594  0.897566  0.901681  0.680441   
98     0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654  0.371901   
99     0.0    0.0    0.0    0.0  0.406694  0.404665  0.400408  0.702479   
100    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261  0.327824   
101   -2.0   -1.0   -2.0    0.0 -0.195740 -0.197769 -0.198675 -0.002755   
102    0.0    0.0    0.0    0.0  0.175456  0.175456  0.176261  0.327824   
103    0.0    0.0    0.0    0.0 -0.526369 -0.524341 -0.526745 -1.005510   
104    0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639  1.071625   
105    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560 -0.873278   
106   -1.0    0.0   -1.0    0.0 -0.538540 -0.538540 -0.541009 -0.730028   
107   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
108   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.035813   
109    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683  0.641873   
110    0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042  0.520661   
111    0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007 -0.079890   
112    0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656 -0.184573   
113   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751  0.019284   
114    0.0    0.0   -1.0    0.0  0.662272  0.660243  0.657157  1.325069   
115    0.0    0.0    0.0    0.0  1.007099  1.005071  1.009679  0.933884   
116    0.0    0.0    0.0    0.0  0.905680  0.903651  0.907794  0.768595   
117   -1.0   -1.0   -1.0    0.0 -0.272819 -0.274848 -0.276108 -0.157025   
118   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.024793   
119   -1.0   -1.0   -1.0    0.0 -0.597363 -0.599391 -0.602140 -1.033058   

        X_140     X_141  ...    X_2866    X_2867    X_2868    X_2869  \
84   1.195011  1.216146  ...  0.064262  0.000000  0.785106  0.304313   
85  -0.868481 -0.903646  ... -0.324895  0.236102  0.201773  0.064288   
86   0.664399  0.908854  ... -0.419956  0.571858 -0.847891 -0.319507   
87   0.342404  0.278646  ...  0.567790  0.921412 -0.816746 -0.348748   
88   0.002268 -0.570312  ... -0.200127  0.620918  0.331402  0.166634   
89  -0.052154  0.054688  ... -3.109893 -3.196578  0.358338 -2.744118   
90  -1.340136 -2.565104  ...  0.016732 -0.363352 -0.050753  0.176381   
91   0.287982  0.205729  ...  0.000000  0.069487  0.000000  0.000000   
92   0.192744  0.039062  ...  0.454905  0.844755 -0.038126 -0.018563   
93  -1.408163 -1.533854  ...  0.046438  0.418545 -0.132402 -0.291484   
94   0.736961  0.252604  ... -0.691772  0.784963  0.207665 -0.766659   
95  -1.058957 -1.471354  ...  0.025644  1.151381  0.819618  0.396911   
96  -0.632653 -0.330729  ...  0.564819 -0.786496 -0.857150  0.201967   
97   0.637188  0.304688  ...  0.255870  0.903014  0.424837 -0.794682   
98   0.551020 -0.690104  ...  0.493524  2.003802  0.717766  0.455394   
99   0.637188  0.835938  ...  0.697014  1.516266  0.134433  0.104496   
100  

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     0.0    0.0    0.0    0.0  0.662272  0.660243  0.657157  1.330579   
85    -1.0   -1.0   -1.0    0.0 -0.597363 -0.599391 -0.602140 -1.011019   
86     0.0    0.0    0.0    0.0  1.017241  1.015213  1.019868  0.707989   
87     0.0    0.0    0.0    0.0  0.879310  0.877282  0.881304  0.366391   
88    -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.008264   
89    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.008264   
90    -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.628099   
91    -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886  0.300275   
92     0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388  0.190083   
93    -1.0    0.0   -1.0    0.0 -0.544625 -0.546653 -0.549159 -1.710744   
94     0.0   -1.0    0.0    0.0  0.996957  0.994929  0.999491  0.785124   
95     0.0    0.0    0.0    0.0 -0.560852 -0.558824 -0.561386 -1.214876   
96     0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709 -0.663912   
97     0.0    0.0    0.0    0.0  0.899594  0.897566  0.901681  0.680441   
98     0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654  0.371901   
99     0.0    0.0    0.0    0.0  0.406694  0.404665  0.400408  0.702479   
100    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261  0.327824   
101   -2.0   -1.0   -2.0    0.0 -0.195740 -0.197769 -0.198675 -0.002755   
102    0.0    0.0    0.0    0.0  0.175456  0.175456  0.176261  0.327824   
103    0.0    0.0    0.0    0.0 -0.526369 -0.524341 -0.526745 -1.005510   
104    0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639  1.071625   
105    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560 -0.873278   
106   -1.0    0.0   -1.0    0.0 -0.538540 -0.538540 -0.541009 -0.730028   
107   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
108   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.035813   
109    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683  0.641873   
110    0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042  0.520661   
111    0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007 -0.079890   
112    0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656 -0.184573   
113   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751  0.019284   
114    0.0    0.0   -1.0    0.0  0.662272  0.660243  0.657157  1.325069   
115    0.0    0.0    0.0    0.0  1.007099  1.005071  1.009679  0.933884   
116    0.0    0.0    0.0    0.0  0.905680  0.903651  0.907794  0.768595   
117   -1.0   -1.0   -1.0    0.0 -0.272819 -0.274848 -0.276108 -0.157025   
118   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.024793   
119   -1.0   -1.0   -1.0    0.0 -0.597363 -0.599391 -0.602140 -1.033058   

        X_140     X_141  ...    X_2866    X_2867    X_2868    X_2869  \
84   1.195011  1.216146  ...  0.064262  0.000000  0.785106  0.304313   
85  -0.868481 -0.903646  ... -0.324895  0.236102  0.201773  0.064288   
86   0.664399  0.908854  ... -0.419956  0.571858 -0.847891 -0.319507   
87   0.342404  0.278646  ...  0.567790  0.921412 -0.816746 -0.348748   
88   0.002268 -0.570312  ... -0.200127  0.620918  0.331402  0.166634   
89  -0.052154  0.054688  ... -3.109893 -3.196578  0.358338 -2.744118   
90  -1.340136 -2.565104  ...  0.016732 -0.363352 -0.050753  0.176381   
91   0.287982  0.205729  ...  0.000000  0.069487  0.000000  0.000000   
92   0.192744  0.039062  ...  0.454905  0.844755 -0.038126 -0.018563   
93  -1.408163 -1.533854  ...  0.046438  0.418545 -0.132402 -0.291484   
94   0.736961  0.252604  ... -0.691772  0.784963  0.207665 -0.766659   
95  -1.058957 -1.471354  ...  0.025644  1.151381  0.819618  0.396911   
96  -0.632653 -0.330729  ...  0.564819 -0.786496 -0.857150  0.201967   
97   0.637188  0.304688  ...  0.255870  0.903014  0.424837 -0.794682   
98   0.551020 -0.690104  ...  0.493524  2.003802  0.717766  0.455394   
99   0.637188  0.835938  ...  0.697014  1.516266  0.134433  0.104496   
100  

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     0.0    0.0    0.0    0.0  0.662272  0.660243  0.657157  1.330579   
85    -1.0   -1.0   -1.0    0.0 -0.597363 -0.599391 -0.602140 -1.011019   
86     0.0    0.0    0.0    0.0  1.017241  1.015213  1.019868  0.707989   
87     0.0    0.0    0.0    0.0  0.879310  0.877282  0.881304  0.366391   
88    -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.008264   
89    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.008264   
90    -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.628099   
91    -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886  0.300275   
92     0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388  0.190083   
93    -1.0    0.0   -1.0    0.0 -0.544625 -0.546653 -0.549159 -1.710744   
94     0.0   -1.0    0.0    0.0  0.996957  0.994929  0.999491  0.785124   
95     0.0    0.0    0.0    0.0 -0.560852 -0.558824 -0.561386 -1.214876   
96     0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709 -0.663912   
97     0.0    0.0    0.0    0.0  0.899594  0.897566  0.901681  0.680441   
98     0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654  0.371901   
99     0.0    0.0    0.0    0.0  0.406694  0.404665  0.400408  0.702479   
100    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261  0.327824   
101   -2.0   -1.0   -2.0    0.0 -0.195740 -0.197769 -0.198675 -0.002755   
102    0.0    0.0    0.0    0.0  0.175456  0.175456  0.176261  0.327824   
103    0.0    0.0    0.0    0.0 -0.526369 -0.524341 -0.526745 -1.005510   
104    0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639  1.071625   
105    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560 -0.873278   
106   -1.0    0.0   -1.0    0.0 -0.538540 -0.538540 -0.541009 -0.730028   
107   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
108   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.035813   
109    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683  0.641873   
110    0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042  0.520661   
111    0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007 -0.079890   
112    0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656 -0.184573   
113   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751  0.019284   
114    0.0    0.0   -1.0    0.0  0.662272  0.660243  0.657157  1.325069   
115    0.0    0.0    0.0    0.0  1.007099  1.005071  1.009679  0.933884   
116    0.0    0.0    0.0    0.0  0.905680  0.903651  0.907794  0.768595   
117   -1.0   -1.0   -1.0    0.0 -0.272819 -0.274848 -0.276108 -0.157025   
118   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.024793   
119   -1.0   -1.0   -1.0    0.0 -0.597363 -0.599391 -0.602140 -1.033058   

        X_140     X_141  ...    X_2866    X_2867    X_2868    X_2869  \
84   1.195011  1.216146  ...  0.064262  0.000000  0.785106  0.304313   
85  -0.868481 -0.903646  ... -0.324895  0.236102  0.201773  0.064288   
86   0.664399  0.908854  ... -0.419956  0.571858 -0.847891 -0.319507   
87   0.342404  0.278646  ...  0.567790  0.921412 -0.816746 -0.348748   
88   0.002268 -0.570312  ... -0.200127  0.620918  0.331402  0.166634   
89  -0.052154  0.054688  ... -3.109893 -3.196578  0.358338 -2.744118   
90  -1.340136 -2.565104  ...  0.016732 -0.363352 -0.050753  0.176381   
91   0.287982  0.205729  ...  0.000000  0.069487  0.000000  0.000000   
92   0.192744  0.039062  ...  0.454905  0.844755 -0.038126 -0.018563   
93  -1.408163 -1.533854  ...  0.046438  0.418545 -0.132402 -0.291484   
94   0.736961  0.252604  ... -0.691772  0.784963  0.207665 -0.766659   
95  -1.058957 -1.471354  ...  0.025644  1.151381  0.819618  0.396911   
96  -0.632653 -0.330729  ...  0.564819 -0.786496 -0.857150  0.201967   
97   0.637188  0.304688  ...  0.255870  0.903014  0.424837 -0.794682   
98   0.551020 -0.690104  ...  0.493524  2.003802  0.717766  0.455394   
99   0.637188  0.835938  ...  0.697014  1.516266  0.134433  0.104496   
100  

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     0.0    0.0    0.0    0.0  0.662272  0.660243  0.657157  1.330579   
85    -1.0   -1.0   -1.0    0.0 -0.597363 -0.599391 -0.602140 -1.011019   
86     0.0    0.0    0.0    0.0  1.017241  1.015213  1.019868  0.707989   
87     0.0    0.0    0.0    0.0  0.879310  0.877282  0.881304  0.366391   
88    -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.008264   
89    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.008264   
90    -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.628099   
91    -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886  0.300275   
92     0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388  0.190083   
93    -1.0    0.0   -1.0    0.0 -0.544625 -0.546653 -0.549159 -1.710744   
94     0.0   -1.0    0.0    0.0  0.996957  0.994929  0.999491  0.785124   
95     0.0    0.0    0.0    0.0 -0.560852 -0.558824 -0.561386 -1.214876   
96     0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709 -0.663912   
97     0.0    0.0    0.0    0.0  0.899594  0.897566  0.901681  0.680441   
98     0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654  0.371901   
99     0.0    0.0    0.0    0.0  0.406694  0.404665  0.400408  0.702479   
100    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261  0.327824   
101   -2.0   -1.0   -2.0    0.0 -0.195740 -0.197769 -0.198675 -0.002755   
102    0.0    0.0    0.0    0.0  0.175456  0.175456  0.176261  0.327824   
103    0.0    0.0    0.0    0.0 -0.526369 -0.524341 -0.526745 -1.005510   
104    0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639  1.071625   
105    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560 -0.873278   
106   -1.0    0.0   -1.0    0.0 -0.538540 -0.538540 -0.541009 -0.730028   
107   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
108   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.035813   
109    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683  0.641873   
110    0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042  0.520661   
111    0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007 -0.079890   
112    0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656 -0.184573   
113   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751  0.019284   
114    0.0    0.0   -1.0    0.0  0.662272  0.660243  0.657157  1.325069   
115    0.0    0.0    0.0    0.0  1.007099  1.005071  1.009679  0.933884   
116    0.0    0.0    0.0    0.0  0.905680  0.903651  0.907794  0.768595   
117   -1.0   -1.0   -1.0    0.0 -0.272819 -0.274848 -0.276108 -0.157025   
118   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.024793   
119   -1.0   -1.0   -1.0    0.0 -0.597363 -0.599391 -0.602140 -1.033058   

        X_140     X_141  ...    X_2866    X_2867    X_2868    X_2869  \
84   1.195011  1.216146  ...  0.064262  0.000000  0.785106  0.304313   
85  -0.868481 -0.903646  ... -0.324895  0.236102  0.201773  0.064288   
86   0.664399  0.908854  ... -0.419956  0.571858 -0.847891 -0.319507   
87   0.342404  0.278646  ...  0.567790  0.921412 -0.816746 -0.348748   
88   0.002268 -0.570312  ... -0.200127  0.620918  0.331402  0.166634   
89  -0.052154  0.054688  ... -3.109893 -3.196578  0.358338 -2.744118   
90  -1.340136 -2.565104  ...  0.016732 -0.363352 -0.050753  0.176381   
91   0.287982  0.205729  ...  0.000000  0.069487  0.000000  0.000000   
92   0.192744  0.039062  ...  0.454905  0.844755 -0.038126 -0.018563   
93  -1.408163 -1.533854  ...  0.046438  0.418545 -0.132402 -0.291484   
94   0.736961  0.252604  ... -0.691772  0.784963  0.207665 -0.766659   
95  -1.058957 -1.471354  ...  0.025644  1.151381  0.819618  0.396911   
96  -0.632653 -0.330729  ...  0.564819 -0.786496 -0.857150  0.201967   
97   0.637188  0.304688  ...  0.255870  0.903014  0.424837 -0.794682   
98   0.551020 -0.690104  ...  0.493524  2.003802  0.717766  0.455394   
99   0.637188  0.835938  ...  0.697014  1.516266  0.134433  0.104496   
100  

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
84     0.0    0.0    0.0    0.0  0.662272  0.660243  0.657157  1.330579   
85    -1.0   -1.0   -1.0    0.0 -0.597363 -0.599391 -0.602140 -1.011019   
86     0.0    0.0    0.0    0.0  1.017241  1.015213  1.019868  0.707989   
87     0.0    0.0    0.0    0.0  0.879310  0.877282  0.881304  0.366391   
88    -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.008264   
89    -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.008264   
90    -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122 -1.628099   
91    -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886  0.300275   
92     0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388  0.190083   
93    -1.0    0.0   -1.0    0.0 -0.544625 -0.546653 -0.549159 -1.710744   
94     0.0   -1.0    0.0    0.0  0.996957  0.994929  0.999491  0.785124   
95     0.0    0.0    0.0    0.0 -0.560852 -0.558824 -0.561386 -1.214876   
96     0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709 -0.663912   
97     0.0    0.0    0.0    0.0  0.899594  0.897566  0.901681  0.680441   
98     0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654  0.371901   
99     0.0    0.0    0.0    0.0  0.406694  0.404665  0.400408  0.702479   
100    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261  0.327824   
101   -2.0   -1.0   -2.0    0.0 -0.195740 -0.197769 -0.198675 -0.002755   
102    0.0    0.0    0.0    0.0  0.175456  0.175456  0.176261  0.327824   
103    0.0    0.0    0.0    0.0 -0.526369 -0.524341 -0.526745 -1.005510   
104    0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639  1.071625   
105    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560 -0.873278   
106   -1.0    0.0   -1.0    0.0 -0.538540 -0.538540 -0.541009 -0.730028   
107   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
108   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675  0.035813   
109    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683  0.641873   
110    0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042  0.520661   
111    0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007 -0.079890   
112    0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656 -0.184573   
113   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751  0.019284   
114    0.0    0.0   -1.0    0.0  0.662272  0.660243  0.657157  1.325069   
115    0.0    0.0    0.0    0.0  1.007099  1.005071  1.009679  0.933884   
116    0.0    0.0    0.0    0.0  0.905680  0.903651  0.907794  0.768595   
117   -1.0   -1.0   -1.0    0.0 -0.272819 -0.274848 -0.276108 -0.157025   
118   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.024793   
119   -1.0   -1.0   -1.0    0.0 -0.597363 -0.599391 -0.602140 -1.033058   

        X_140     X_141  ...    X_2866    X_2867    X_2868    X_2869  \
84   1.195011  1.216146  ...  0.064262  0.000000  0.785106  0.304313   
85  -0.868481 -0.903646  ... -0.324895  0.236102  0.201773  0.064288   
86   0.664399  0.908854  ... -0.419956  0.571858 -0.847891 -0.319507   
87   0.342404  0.278646  ...  0.567790  0.921412 -0.816746 -0.348748   
88   0.002268 -0.570312  ... -0.200127  0.620918  0.331402  0.166634   
89  -0.052154  0.054688  ... -3.109893 -3.196578  0.358338 -2.744118   
90  -1.340136 -2.565104  ...  0.016732 -0.363352 -0.050753  0.176381   
91   0.287982  0.205729  ...  0.000000  0.069487  0.000000  0.000000   
92   0.192744  0.039062  ...  0.454905  0.844755 -0.038126 -0.018563   
93  -1.408163 -1.533854  ...  0.046438  0.418545 -0.132402 -0.291484   
94   0.736961  0.252604  ... -0.691772  0.784963  0.207665 -0.766659   
95  -1.058957 -1.471354  ...  0.025644  1.151381  0.819618  0.396911   
96  -0.632653 -0.330729  ...  0.564819 -0.786496 -0.857150  0.201967   
97   0.637188  0.304688  ...  0.255870  0.903014  0.424837 -0.794682   
98   0.551020 -0.690104  ...  0.493524  2.003802  0.717766  0.455394   
99   0.637188  0.835938  ...  0.697014  1.516266  0.134433  0.104496   
100  

In [64]:
T05_final_regression_model = finalize_model(T05_model_et)

In [65]:
T05_prediction = predict_model(T05_final_regression_model, data=T05_data)
T05_prediction

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
0     -1.0    0.0   -1.0    0.0  0.211968  0.209939  0.206826  0.498623   
1      0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709 -0.663912   
2      0.0    0.0   -1.0    0.0 -0.412779 -0.414807 -0.416709 -0.713499   
3      0.0    0.0    0.0    0.0 -0.410751 -0.412779 -0.414671 -0.856749   
4     -1.0    0.0   -1.0    0.0 -0.256592 -0.258621 -0.259806 -0.426997   
..     ...    ...    ...    ...       ...       ...       ...       ...   
115   -1.0    0.0   -1.0    0.0  0.917850  0.915821  0.920020  0.438017   
116    0.0    0.0    0.0    0.0 -0.526369 -0.524341 -0.526745 -1.005510   
117    0.0    0.0    0.0    0.0 -0.343813 -0.341785 -0.343352 -0.719008   
118    0.0    0.0    0.0    0.0 -0.343813 -0.341785 -0.343352 -0.724518   
119    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560 -0.873278   

        X_140     X_141  ...  X_2865    X_2866    X_2867    X_2868    X_2869  \
0    0.414966  0.752604  ...     0.0  0.293004 -0.513599  0.392008  0.220243   
1   -0.632653 -0.330729  ...     1.0  0.564819 -0.786496 -0.857150  0.201967   
2   -0.664399 -0.440104  ...     0.0 -0.709596 -0.665379  0.400426  0.154450   
3   -0.773243 -0.617188  ...     0.0  0.000000  0.069487  0.000000  0.000000   
4   -0.392290 -0.221354  ...   -10.0 -0.012975  0.545795 -0.705635  0.187347   
..        ...       ...  ...     ...       ...       ...       ...       ...   
115  0.414966  0.268229  ...     0.0 -1.339377  0.712906  0.754803  0.201967   
116 -0.895692 -0.658854  ...     1.0 -0.712566 -0.611351 -0.111662 -0.866909   
117 -0.623583 -0.351562  ...     2.0  0.058321  0.334223 -0.740147 -0.213506   
118 -0.628118 -0.752604  ...     0.0 -0.712566 -0.611351 -0.111662 -0.866909   
119 -0.746032 -0.700521  ...   -10.0 -0.712566 -0.611351 -0.111662 -0.866909   

       X_2870  X_2871      HOUR  DAY_OF_WEEK  prediction_label  
0    0.567287     0.0  1.111111         -0.4          0.521524  
1    0.306529     0.0  1.333333         -0.2          0.516711  
2    0.603349     0.0  1.333333         -0.2          0.519451  
3   -0.147839     0.0  1.444444         -0.2          0.518960  
4    0.054093     0.0 -0.777778          0.6          0.519810  
..        ...     ...       ...          ...               ...  
115  0.165054     0.0 -0.111111         -0.4          0.537560  
116  0.668483     0.0  0.888889          0.6          0.543957  
117 -0.517355     0.0  0.555556          0.0          0.550340  
118  0.668483     0.0  0.555556          0.0          0.551949  
119  0.668483     0.0  0.111111          0.2          0.539611  

[120 rows x 1959 columns]

In [66]:
T05_datas = T05_prediction['prediction_label']
T05_datas = pd.DataFrame(T05_datas.values, columns = ['Y_Quality'])
T05_datas

Y_Quality
0     0.521524
1     0.516711
2     0.519451
3     0.518960
4     0.519810
..         ...
115   0.537560
116   0.543957
117   0.550340
118   0.551949
119   0.539611

[120 rows x 1 columns]

In [67]:
T05y_idx= T05_class.index
T05y_idx = pd.DataFrame(T05y_idx, columns = ['index'])
T05_datas = pd.concat([T05y_idx, T05_datas], axis = 1)
T05_datas = T05_datas.set_index('index')
T05_datas

Y_Quality
index           
34      0.521524
109     0.516711
110     0.519451
111     0.518960
131     0.519810
...          ...
261     0.537560
316     0.543957
355     0.550340
356     0.551949
369     0.539611

[120 rows x 1 columns]

In [68]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T05_datas, 
                   target=T05_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [69]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbc = create_model('gbc', fold = 5)
T05_total_models.append(T05_model_gbc)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [70]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbc = tune_model(T05_model_gbc, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [71]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbc, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]
T05_tuned_models

[LGBMClassifier(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
                importance_type='split', learning_rate=0.1, max_depth=-1,
                min_child_samples=20, min_child_weight=0.001, min_split_gain=0.0,
                n_estimators=100, n_jobs=-1, num_leaves=31, objective=None,
                random_state=414, reg_alpha=0.0, reg_lambda=0.0, silent=True,
                subsample=1.0, subsample_for_bin=200000, subsample_freq=0),
 RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                        criterion='gini', max_depth=None, max_features='auto',
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.0, min_samples_leaf=1,
                        min_samples_split=2, min_weight_fraction_leaf=0.0,
                        n_estimators=100, n_jobs=-1, oob_score=False,
                        random_state=414, verbose=0, warm_start=False),
 GradientBoostingClassifier(ccp

In [72]:
for model in T05_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.519332        0                 0            0.9920
85    0.524781        0                 0            0.6880
86    0.527944        1                 1            0.9956
87    0.519451        0                 0            0.9920
88    0.550340        2                 2            0.9903
89    0.513751        0                 0            0.9920
90    0.527332        1                 1            0.9956
91    0.544129        2                 2            0.9903
92    0.527976        1                 1            0.9956
93    0.528186        1                 1            0.9956
94    0.525046        0                 0            0.6880
95    0.535405        2                 2            0.6814
96    0.531821        1                 1            0.9954
97    0.529681        1                 1            0.9956
98    0.559464        2                 2            0.9903
99    0.525494        1                 1            0.9946
100   0.527398        1                 1            0.9956
101   0.562770        2                 2            0.9903
102   0.539611        2                 2            0.9903
103   0.519406        0                 0            0.9920
104   0.531503        1                 1            0.9954
105   0.520856        0                 0            0.9920
106   0.547592        2                 2            0.9903
107   0.533665        1                 1            0.9917
108   0.521051        0                 0            0.9920
109   0.543957        2                 2            0.9903
110   0.560568        2                 2            0.9903
111   0.523383        0                 0            0.9920
112   0.520911        0                 0            0.9920
113   0.522460        0                 0            0.9920
114   0.524022        0                 0            0.9920
115   0.531267        1                 1            0.9956
116   0.534054        1                 1            0.9917
117   0.532170        1                 1            0.9950
118   0.531254        1                 1            0.9956
119   0.537560        2                 2            0.9903

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.519332        0                 0              1.00
85    0.524781        0                 0              0.93
86    0.527944        1                 1              1.00
87    0.519451        0                 0              1.00
88    0.550340        2                 2              1.00
89    0.513751        0                 0              1.00
90    0.527332        1                 1              1.00
91    0.544129        2                 2              1.00
92    0.527976        1                 1              1.00
93    0.528186        1                 1              1.00
94    0.525046        0                 1              0.95
95    0.535405        2                 2              0.67
96    0.531821        1                 1              1.00
97    0.529681        1                 1              1.00
98    0.559464        2                 2              1.00
99    0.525494        1                 1              0.99
100   0.527398        1                 1              1.00
101   0.562770        2                 2              1.00
102   0.539611        2                 2              1.00
103   0.519406        0                 0              1.00
104   0.531503        1                 1              1.00
105   0.520856        0                 0              1.00
106   0.547592        2                 2              1.00
107   0.533665        1                 1              1.00
108   0.521051        0                 0              1.00
109   0.543957        2                 2              1.00
110   0.560568        2                 2              1.00
111   0.523383        0                 0              1.00
112   0.520911        0                 0              1.00
113   0.522460        0                 0              1.00
114   0.524022        0                 0              0.99
115   0.531267        1                 1              1.00
116   0.534054        1                 1              1.00
117   0.532170        1                 1              1.00
118   0.531254        1                 1              1.00
119   0.537560        2                 2              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.519332        0                 0            0.9942
85    0.524781        0                 0            0.9788
86    0.527944        1                 1            0.9917
87    0.519451        0                 0            0.9942
88    0.550340        2                 2            0.9918
89    0.513751        0                 0            0.9942
90    0.527332        1                 1            0.9917
91    0.544129        2                 2            0.9918
92    0.527976        1                 1            0.9917
93    0.528186        1                 1            0.9917
94    0.525046        0                 1            0.9595
95    0.535405        2                 1            0.5235
96    0.531821        1                 1            0.9917
97    0.529681        1                 1            0.9917
98    0.559464        2                 2            0.9918
99    0.525494        1                 1            0.9875
100   0.527398        1                 1            0.9917
101   0.562770        2                 2            0.9918
102   0.539611        2                 2            0.9918
103   0.519406        0                 0            0.9942
104   0.531503        1                 1            0.9917
105   0.520856        0                 0            0.9942
106   0.547592        2                 2            0.9918
107   0.533665        1                 1            0.9917
108   0.521051        0                 0            0.9942
109   0.543957        2                 2            0.9918
110   0.560568        2                 2            0.9918
111   0.523383        0                 0            0.9942
112   0.520911        0                 0            0.9942
113   0.522460        0                 0            0.9942
114   0.524022        0                 0            0.9923
115   0.531267        1                 1            0.9917
116   0.534054        1                 1            0.9917
117   0.532170        1                 1            0.9917
118   0.531254        1                 1            0.9917
119   0.537560        2                 2            0.9918

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.519332        0                 0              1.00
85    0.524781        0                 0              0.62
86    0.527944        1                 1              1.00
87    0.519451        0                 0              1.00
88    0.550340        2                 2              1.00
89    0.513751        0                 0              1.00
90    0.527332        1                 1              1.00
91    0.544129        2                 2              1.00
92    0.527976        1                 1              1.00
93    0.528186        1                 1              1.00
94    0.525046        0                 1              0.94
95    0.535405        2                 1              0.56
96    0.531821        1                 1              1.00
97    0.529681        1                 1              1.00
98    0.559464        2                 2              1.00
99    0.525494        1                 1              1.00
100   0.527398        1                 1              1.00
101   0.562770        2                 2              1.00
102   0.539611        2                 2              1.00
103   0.519406        0                 0              1.00
104   0.531503        1                 1              1.00
105   0.520856        0                 0              1.00
106   0.547592        2                 2              1.00
107   0.533665        1                 1              1.00
108   0.521051        0                 0              1.00
109   0.543957        2                 2              1.00
110   0.560568        2                 2              1.00
111   0.523383        0                 0              1.00
112   0.520911        0                 0              1.00
113   0.522460        0                 0              1.00
114   0.524022        0                 0              1.00
115   0.531267        1                 1              1.00
116   0.534054        1                 1              1.00
117   0.532170        1                 1              1.00
118   0.531254        1                 1              1.00
119   0.537560        2                 2              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.519332        0                 0            0.9991
85    0.524781        0                 0            0.9746
86    0.527944        1                 1            0.9991
87    0.519451        0                 0            0.9991
88    0.550340        2                 2            0.9984
89    0.513751        0                 0            0.9983
90    0.527332        1                 1            0.9991
91    0.544129        2                 2            0.9987
92    0.527976        1                 1            0.9992
93    0.528186        1                 1            0.9992
94    0.525046        0                 1            0.9799
95    0.535405        2                 2            0.9784
96    0.531821        1                 1            0.9990
97    0.529681        1                 1            0.9992
98    0.559464        2                 2            0.9981
99    0.525494        1                 1            0.9975
100   0.527398        1                 1            0.9991
101   0.562770        2                 2            0.9981
102   0.539611        2                 2            0.9988
103   0.519406        0                 0            0.9991
104   0.531503        1                 1            0.9991
105   0.520856        0                 0            0.9991
106   0.547592        2                 2            0.9984
107   0.533665        1                 1            0.9962
108   0.521051        0                 0            0.9991
109   0.543957        2                 2            0.9987
110   0.560568        2                 2            0.9981
111   0.523383        0                 0            0.9989
112   0.520911        0                 0            0.9991
113   0.522460        0                 0            0.9990
114   0.524022        0                 0            0.9985
115   0.531267        1                 1            0.9991
116   0.534054        1                 1            0.9906
117   0.532170        1                 1            0.9989
118   0.531254        1                 1            0.9991
119   0.537560        2                 2            0.9975

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.519332        0                 0            0.9840
85    0.524781        0                 0            0.9840
86    0.527944        1                 1            0.9824
87    0.519451        0                 0            0.9840
88    0.550340        2                 2            0.9803
89    0.513751        0                 0            0.9840
90    0.527332        1                 1            0.9817
91    0.544129        2                 2            0.9803
92    0.527976        1                 1            0.9824
93    0.528186        1                 1            0.9824
94    0.525046        0                 1            0.9773
95    0.535405        2                 2            0.9803
96    0.531821        1                 1            0.9810
97    0.529681        1                 1            0.9901
98    0.559464        2                 2            0.9803
99    0.525494        1                 1            0.9804
100   0.527398        1                 1            0.9817
101   0.562770        2                 2            0.9803
102   0.539611        2                 2            0.9803
103   0.519406        0                 0            0.9840
104   0.531503        1                 1            0.9810
105   0.520856        0                 0            0.9840
106   0.547592        2                 2            0.9803
107   0.533665        1                 1            0.9784
108   0.521051        0                 0            0.9840
109   0.543957        2                 2            0.9803
110   0.560568        2                 2            0.9803
111   0.523383        0                 0            0.9840
112   0.520911        0                 0            0.9840
113   0.522460        0                 0            0.9840
114   0.524022        0                 0            0.9840
115   0.531267        1                 1            0.9816
116   0.534054        1                 1            0.9784
117   0.532170        1                 1            0.9810
118   0.531254        1                 1            0.9816
119   0.537560        2                 2            0.9803

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.519332        0                 0               1.0
85    0.524781        0                 0               1.0
86    0.527944        1                 1               1.0
87    0.519451        0                 0               1.0
88    0.550340        2                 2               1.0
89    0.513751        0                 0               1.0
90    0.527332        1                 1               1.0
91    0.544129        2                 2               1.0
92    0.527976        1                 1               1.0
93    0.528186        1                 1               1.0
94    0.525046        0                 1               1.0
95    0.535405        2                 2               1.0
96    0.531821        1                 1               1.0
97    0.529681        1                 1               1.0
98    0.559464        2                 2               1.0
99    0.525494        1                 1               1.0
100   0.527398        1                 1               1.0
101   0.562770        2                 2               1.0
102   0.539611        2                 2               1.0
103   0.519406        0                 0               1.0
104   0.531503        1                 1               1.0
105   0.520856        0                 0               1.0
106   0.547592        2                 2               1.0
107   0.533665        1                 1               1.0
108   0.521051        0                 0               1.0
109   0.543957        2                 2               1.0
110   0.560568        2                 2               1.0
111   0.523383        0                 0               1.0
112   0.520911        0                 0               1.0
113   0.522460        0                 0               1.0
114   0.524022        0                 0               1.0
115   0.531267        1                 1               1.0
116   0.534054        1                 1               1.0
117   0.532170        1                 1               1.0
118   0.531254        1                 1               1.0
119   0.537560        2                 2               1.0

In [73]:
T05_final_classification_model = finalize_model(T05_model_lightgbm)

In [74]:
T05_prediction = predict_model(T05_final_classification_model, data=T05_datas)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)
T05_prediction

Y_Quality  prediction_label  prediction_score
0     0.521524                 0            0.9981
1     0.516711                 0            0.9984
2     0.519451                 0            0.9984
3     0.518960                 0            0.9984
4     0.519810                 0            0.9984
..         ...               ...               ...
115   0.537560                 2            0.9999
116   0.543957                 2            0.9999
117   0.550340                 2            0.9999
118   0.551949                 2            0.9999
119   0.539611                 2            0.9999

[120 rows x 3 columns]

In [75]:
T05_y_class = pd.DataFrame(T05_class, columns = ['Y_Class'])
T05_idx = T05_y_class.index
T05_y_class = T05_y_class.reset_index()
T05_prediction = pd.concat([T05_prediction, T05_y_class], axis = 1)
T05_prediction = T05_prediction.set_index('index')
T05_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [76]:
T05_prediction

Y_Quality  prediction_label  prediction_score
index                                               
34      0.521524                 0            0.9981
109     0.516711                 0            0.9984
110     0.519451                 0            0.9984
111     0.518960                 0            0.9984
131     0.519810                 0            0.9984
...          ...               ...               ...
261     0.537560                 2            0.9999
316     0.543957                 2            0.9999
355     0.550340                 2            0.9999
356     0.551949                 2            0.9999
369     0.539611                 2            0.9999

[120 rows x 3 columns]

# T01

In [77]:
T01_class = T01['Y_Class']
T01_target = T01['Y_Quality']
T01_data = T01.drop(['Y_Class', 'Y_Quality'], axis = 1)
T01_data

X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  X_254  X_255  \
28     1.0   89.0    0.0   45.0   11.0   90.0   45.0   11.0   42.0    2.0   
66     2.0   88.0    0.0   45.0   11.0  127.0   45.0   11.0   42.0    2.0   
116    1.0   95.0    0.0   45.0   11.0    2.0   45.0   11.0   42.0    2.0   
118    1.0   91.0    0.0   45.0   11.0    2.0   45.0   12.0   42.0    2.0   
123    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   42.0    2.0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
293    1.0   94.0    5.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   
419    1.0   93.0   74.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   
471    1.0   93.0  103.0   45.0   11.0    0.0   45.0   12.0   51.0    2.0   
472    1.0   90.0  103.0   45.0   11.0    0.0   45.0   12.0   51.0    2.0   
531    1.0   90.0  142.0   45.0   11.0    0.0   45.0   12.0   51.0    2.0   

     ...      X_2858  X_2859  X_2860      X_2861  X_2862  X_2863      X_2864  \
28   ...  182.758621   175.7   182.0  174.727586   160.5   446.0  429.716981   
66   ...  197.131034   189.9   190.4  184.720690   180.0   466.0  449.962264   
116  ...  174.489286   171.5   179.7  170.342857   157.4   466.0  450.115385   
118  ...  172.833333   154.6   175.5  163.003704   140.3   466.0  449.423077   
123  ...  171.010714   163.1   177.8  167.967857   158.4   466.0  447.750000   
..   ...         ...     ...     ...         ...     ...     ...         ...   
293  ...  197.225000   182.1   172.9  167.453571   159.7   466.0  445.942308   
419  ...  186.131034   177.4   170.6  163.220690   146.8   466.0  442.320755   
471  ...  202.821429   196.8   185.7  176.457143   166.3   466.0  447.153846   
472  ...  198.279310   180.6   186.9  176.134483   162.9   457.0  440.320755   
531  ...  190.407143   181.1   192.6  185.207143   173.2   466.0  446.038461   

     X_2865  HOUR  DAY_OF_WEEK  
28    413.0    20            7  
66    434.0    21            6  
116   432.0    15            4  
118   432.0    17            4  
123   432.0    13            5  
..      ...   ...          ...  
293   424.0    10            6  
419   422.0     2            4  
471   423.0     1            2  
472   422.0     1            2  
531   427.0    15            1  

[129 rows x 880 columns]

In [78]:
T_01c = T01_data.columns
T_01scaler = RobustScaler()
T_01scaled = T_01scaler.fit_transform(T01_data)
T01_data = pd.DataFrame(T_01scaled, columns = T_01c)
T01_data

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
0      0.0  -0.25 -0.054348    0.0    0.0  1.011236    0.0   -1.0   -1.0   
1      1.0  -0.50 -0.054348    0.0    0.0  1.426966    0.0   -1.0   -1.0   
2      0.0   1.25 -0.054348    0.0    0.0  0.022472    0.0   -1.0   -1.0   
3      0.0   0.25 -0.054348    0.0    0.0  0.022472    0.0    0.0   -1.0   
4      1.0   0.75 -0.054348    0.0    0.0  0.089888    0.0   -1.0   -1.0   
..     ...    ...       ...    ...    ...       ...    ...    ...    ...   
124    0.0   1.00  0.000000    0.0    1.0  0.000000    0.0    0.0    0.0   
125    0.0   0.75  0.750000    0.0    1.0  0.000000    0.0    0.0    0.0   
126    0.0   0.75  1.065217    0.0    0.0  0.000000    0.0    0.0    0.0   
127    0.0   0.00  1.065217    0.0    0.0  0.000000    0.0    0.0    0.0   
128    0.0   0.00  1.489130    0.0    0.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2858    X_2859    X_2860    X_2861    X_2862  X_2863  \
0      0.0  ... -0.390876  0.000000 -0.053030  0.321839  0.041096    -1.9   
1      0.0  ...  0.533739  0.735751  0.583333  1.154598  1.376712     0.1   
2      0.0  ... -0.922864 -0.217617 -0.227273 -0.043555 -0.171233     0.1   
3      0.0  ... -1.029396 -1.093264 -0.545455 -0.655151 -1.342466     0.1   
4      0.0  ... -1.146650 -0.652850 -0.371212 -0.241472 -0.102740     0.1   
..     ...  ...       ...       ...       ...       ...       ...     ...   
124    0.0  ...  0.539784  0.331606 -0.742424 -0.284329 -0.013699     0.1   
125    0.0  ... -0.173920  0.088083 -0.916667 -0.637069 -0.897260     0.1   
126    0.0  ...  0.899817  1.093264  0.227273  0.465969  0.438356     0.1   
127    0.0  ...  0.607611  0.253886  0.318182  0.439080  0.205479    -0.8   
128    0.0  ...  0.101173  0.279793  0.750000  1.195135  0.910959     0.1   

       X_2864  X_2865      HOUR  DAY_OF_WEEK  
0   -1.452964    -5.0  0.777778     0.666667  
1    0.880914     5.5  0.888889     0.333333  
2    0.898565     4.5  0.222222    -0.333333  
3    0.818756     4.5  0.444444    -0.333333  
4    0.625884     4.5  0.000000     0.000000  
..        ...     ...       ...          ...  
124  0.417493     0.5 -0.333333     0.333333  
125  0.000000    -0.5 -1.222222    -0.333333  
126  0.557159     0.0 -1.333333    -1.000000  
127 -0.230560    -0.5 -1.333333    -1.000000  
128  0.428577     2.0  0.222222    -1.333333  

[129 rows x 880 columns]

In [79]:
T01_y_class = pd.DataFrame(T01_target, columns = ['Y_Quality'])
T01_idx = T01_y_class.index
T01_y_class = T01_y_class.reset_index()
T01_data = pd.concat([T01_data, T01_y_class], axis = 1)
T01_data = T01_data.set_index('index')
T01_data.drop(['Y_Quality'], axis = 1, inplace = True)
T01_data

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
index                                                                        
28       0.0  -0.25 -0.054348    0.0    0.0  1.011236    0.0   -1.0   -1.0   
66       1.0  -0.50 -0.054348    0.0    0.0  1.426966    0.0   -1.0   -1.0   
116      0.0   1.25 -0.054348    0.0    0.0  0.022472    0.0   -1.0   -1.0   
118      0.0   0.25 -0.054348    0.0    0.0  0.022472    0.0    0.0   -1.0   
123      1.0   0.75 -0.054348    0.0    0.0  0.089888    0.0   -1.0   -1.0   
...      ...    ...       ...    ...    ...       ...    ...    ...    ...   
293      0.0   1.00  0.000000    0.0    1.0  0.000000    0.0    0.0    0.0   
419      0.0   0.75  0.750000    0.0    1.0  0.000000    0.0    0.0    0.0   
471      0.0   0.75  1.065217    0.0    0.0  0.000000    0.0    0.0    0.0   
472      0.0   0.00  1.065217    0.0    0.0  0.000000    0.0    0.0    0.0   
531      0.0   0.00  1.489130    0.0    0.0  0.000000    0.0    0.0    0.0   

       X_255  ...    X_2858    X_2859    X_2860    X_2861    X_2862  X_2863  \
index         ...                                                             
28       0.0  ... -0.390876  0.000000 -0.053030  0.321839  0.041096    -1.9   
66       0.0  ...  0.533739  0.735751  0.583333  1.154598  1.376712     0.1   
116      0.0  ... -0.922864 -0.217617 -0.227273 -0.043555 -0.171233     0.1   
118      0.0  ... -1.029396 -1.093264 -0.545455 -0.655151 -1.342466     0.1   
123      0.0  ... -1.146650 -0.652850 -0.371212 -0.241472 -0.102740     0.1   
...      ...  ...       ...       ...       ...       ...       ...     ...   
293      0.0  ...  0.539784  0.331606 -0.742424 -0.284329 -0.013699     0.1   
419      0.0  ... -0.173920  0.088083 -0.916667 -0.637069 -0.897260     0.1   
471      0.0  ...  0.899817  1.093264  0.227273  0.465969  0.438356     0.1   
472      0.0  ...  0.607611  0.253886  0.318182  0.439080  0.205479    -0.8   
531      0.0  ...  0.101173  0.279793  0.750000  1.195135  0.910959     0.1   

         X_2864  X_2865      HOUR  DAY_OF_WEEK  
index                                           
28    -1.452964    -5.0  0.777778     0.666667  
66     0.880914     5.5  0.888889     0.333333  
116    0.898565     4.5  0.222222    -0.333333  
118    0.818756     4.5  0.444444    -0.333333  
123    0.625884     4.5  0.000000     0.000000  
...         ...     ...       ...          ...  
293    0.417493     0.5 -0.333333     0.333333  
419    0.000000    -0.5 -1.222222    -0.333333  
471    0.557159     0.0 -1.333333    -1.000000  
472   -0.230560    -0.5 -1.333333    -1.000000  
531    0.428577     2.0  0.222222    -1.333333  

[129 rows x 880 columns]

In [80]:
from pycaret.regression import *
setup_rgs = setup(data = T01_data, target = T01_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [81]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbr = create_model('gbr', fold = 5)
T01_total_models.append(T01_model_gbr)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [82]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbr = tune_model(T01_model_gbr, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [83]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbr, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]
T01_tuned_models

[LGBMRegressor(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
               importance_type='split', learning_rate=0.1, max_depth=-1,
               min_child_samples=20, min_child_weight=0.001, min_split_gain=0.0,
               n_estimators=100, n_jobs=-1, num_leaves=31, objective=None,
               random_state=414, reg_alpha=0.0, reg_lambda=0.0, silent=True,
               subsample=1.0, subsample_for_bin=200000, subsample_freq=0),
 RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='squared_error',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       max_samples=None, min_impurity_decrease=0.0,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=-1,
                       oob_score=False, random_state=414, verbose=0,
                       warm_start=False),
 GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0, c

In [84]:
for model in T01_tuned_models:
    display(predict_model(model))

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     0.0   1.25 -0.054348    0.0    0.0  1.662921    0.0   -1.0   -1.0   
91     0.0  -0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
92     1.0   0.00 -0.054348    0.0    0.0  1.370787    0.0   -1.0   -1.0   
93     0.0  -0.50  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
94     0.0   0.00  0.858696    0.0    0.0  0.000000    0.0    0.0    0.0   
95     0.0   1.50  0.239130    0.0    1.0  0.000000    0.0    0.0    0.0   
96     0.0   0.25  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
97     0.0  -0.25  0.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
98     0.0   1.25  1.521739    0.0    0.0  0.000000    0.0    0.0    0.0   
99     0.0   1.00  0.000000    0.0    1.0  0.000000    0.0    0.0    0.0   
100    0.0  -0.75  1.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
101    0.0   1.25  0.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
102    1.0  -0.75 -0.054348    0.0    0.0  1.280899    0.0   -1.0   -1.0   
103    0.0   0.25  1.445652    0.0    1.0  0.000000    0.0    0.0    0.0   
104    1.0   0.25  0.826087    0.0    1.0  0.000000    0.0    0.0    0.0   
105    1.0   1.25  1.793478    0.0    1.0  0.000000    0.0    0.0    0.0   
106    0.0   0.00  1.065217    0.0    0.0  0.000000    0.0    0.0    0.0   
107    0.0  -0.50  0.532609    0.0    0.0  0.000000    0.0    0.0    0.0   
108    1.0  -0.75 -0.054348    0.0    0.0  1.415730    0.0   -1.0   -1.0   
109    1.0   0.75  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
110    1.0  -0.50 -0.054348    0.0    0.0  1.426966    0.0   -1.0   -1.0   
111    0.0   0.00 -0.054348    0.0    0.0  1.404494    0.0   -1.0   -1.0   
112    0.0   0.75 -0.010870    0.0    0.0  0.000000    0.0    0.0    0.0   
113    0.0  -0.50  0.847826    0.0    1.0  0.000000    0.0    0.0    0.0   
114   10.0   0.00 -0.054348    0.0    0.0  0.483146    0.0   -1.0   -1.0   
115    1.0  -0.25  0.673913    0.0    0.0  0.000000    0.0    0.0    0.0   
116    0.0  -0.25 -0.054348    0.0    0.0  1.078652    0.0   -1.0   -1.0   
117    0.0   1.25  1.750000    0.0    0.0  0.000000    0.0    0.0    0.0   
118    1.0   0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
119    0.0   0.00 -0.054348    0.0    0.0  0.977528    0.0   -1.0   -1.0   
120    0.0  -0.75 -0.054348    0.0    0.0  0.123596    0.0   -1.0   -1.0   
121    0.0   1.50 -0.054348    0.0    0.0  1.044944    0.0   -1.0   -1.0   
122    0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
123    0.0   1.50 -0.032609    0.0    1.0  0.000000    0.0    0.0    0.0   
124    0.0   0.25 -0.043478    0.0    1.0  0.000000    0.0    0.0    0.0   
125    0.0   1.00  1.228261    0.0    1.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.50  0.076087    0.0    1.0  0.000000    0.0    0.0    0.0   
127    0.0   1.25 -0.054348    0.0    0.0  1.741573    0.0   -1.0   -1.0   
128    0.0  -0.25  1.597826    0.0    1.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2860    X_2861    X_2862  X_2863    X_2864  X_2865  \
90     0.0  ...  1.227273  1.470690  1.445205    -0.9 -0.334965    -0.5   
91     0.0  ...  0.098485  0.551385  0.698630     0.1  0.650270     4.5   
92     0.0  ...  1.401515  1.701724  1.493151     0.1  0.300163     0.5   
93     0.0  ... -0.174242 -0.090281  0.109589     0.1  0.488434     0.0   
94     0.0  ...  1.204545  1.235909  0.623288     0.0  0.820973     4.5   
95     0.0  ...  0.492424  1.090671  1.342466     0.1 -0.076881     0.0   
96     0.0  ...  0.643939  0.724005  0.506849     0.1  0.406408     0.0   
97     0.0  ...  0.454545  0.215374 -0.410959     0.1  0.508387     0.0   
98     0.0  ... -0.113636 -0.268853 -0.130137    -0.9 -0.271971    -0.5   
99     0.0  ... -0.742424 -0.284329 -0.013699     0.1  0.417493     0.5   
100    0.0  ...  0.431818  0.363290  0.000000    -1.9 -1.369348    -5.0   
101    0.0  ... -0.340909  0.038985 -0.383562    -0.9 -0.132304 

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     0.0   1.25 -0.054348    0.0    0.0  1.662921    0.0   -1.0   -1.0   
91     0.0  -0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
92     1.0   0.00 -0.054348    0.0    0.0  1.370787    0.0   -1.0   -1.0   
93     0.0  -0.50  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
94     0.0   0.00  0.858696    0.0    0.0  0.000000    0.0    0.0    0.0   
95     0.0   1.50  0.239130    0.0    1.0  0.000000    0.0    0.0    0.0   
96     0.0   0.25  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
97     0.0  -0.25  0.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
98     0.0   1.25  1.521739    0.0    0.0  0.000000    0.0    0.0    0.0   
99     0.0   1.00  0.000000    0.0    1.0  0.000000    0.0    0.0    0.0   
100    0.0  -0.75  1.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
101    0.0   1.25  0.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
102    1.0  -0.75 -0.054348    0.0    0.0  1.280899    0.0   -1.0   -1.0   
103    0.0   0.25  1.445652    0.0    1.0  0.000000    0.0    0.0    0.0   
104    1.0   0.25  0.826087    0.0    1.0  0.000000    0.0    0.0    0.0   
105    1.0   1.25  1.793478    0.0    1.0  0.000000    0.0    0.0    0.0   
106    0.0   0.00  1.065217    0.0    0.0  0.000000    0.0    0.0    0.0   
107    0.0  -0.50  0.532609    0.0    0.0  0.000000    0.0    0.0    0.0   
108    1.0  -0.75 -0.054348    0.0    0.0  1.415730    0.0   -1.0   -1.0   
109    1.0   0.75  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
110    1.0  -0.50 -0.054348    0.0    0.0  1.426966    0.0   -1.0   -1.0   
111    0.0   0.00 -0.054348    0.0    0.0  1.404494    0.0   -1.0   -1.0   
112    0.0   0.75 -0.010870    0.0    0.0  0.000000    0.0    0.0    0.0   
113    0.0  -0.50  0.847826    0.0    1.0  0.000000    0.0    0.0    0.0   
114   10.0   0.00 -0.054348    0.0    0.0  0.483146    0.0   -1.0   -1.0   
115    1.0  -0.25  0.673913    0.0    0.0  0.000000    0.0    0.0    0.0   
116    0.0  -0.25 -0.054348    0.0    0.0  1.078652    0.0   -1.0   -1.0   
117    0.0   1.25  1.750000    0.0    0.0  0.000000    0.0    0.0    0.0   
118    1.0   0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
119    0.0   0.00 -0.054348    0.0    0.0  0.977528    0.0   -1.0   -1.0   
120    0.0  -0.75 -0.054348    0.0    0.0  0.123596    0.0   -1.0   -1.0   
121    0.0   1.50 -0.054348    0.0    0.0  1.044944    0.0   -1.0   -1.0   
122    0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
123    0.0   1.50 -0.032609    0.0    1.0  0.000000    0.0    0.0    0.0   
124    0.0   0.25 -0.043478    0.0    1.0  0.000000    0.0    0.0    0.0   
125    0.0   1.00  1.228261    0.0    1.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.50  0.076087    0.0    1.0  0.000000    0.0    0.0    0.0   
127    0.0   1.25 -0.054348    0.0    0.0  1.741573    0.0   -1.0   -1.0   
128    0.0  -0.25  1.597826    0.0    1.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2860    X_2861    X_2862  X_2863    X_2864  X_2865  \
90     0.0  ...  1.227273  1.470690  1.445205    -0.9 -0.334965    -0.5   
91     0.0  ...  0.098485  0.551385  0.698630     0.1  0.650270     4.5   
92     0.0  ...  1.401515  1.701724  1.493151     0.1  0.300163     0.5   
93     0.0  ... -0.174242 -0.090281  0.109589     0.1  0.488434     0.0   
94     0.0  ...  1.204545  1.235909  0.623288     0.0  0.820973     4.5   
95     0.0  ...  0.492424  1.090671  1.342466     0.1 -0.076881     0.0   
96     0.0  ...  0.643939  0.724005  0.506849     0.1  0.406408     0.0   
97     0.0  ...  0.454545  0.215374 -0.410959     0.1  0.508387     0.0   
98     0.0  ... -0.113636 -0.268853 -0.130137    -0.9 -0.271971    -0.5   
99     0.0  ... -0.742424 -0.284329 -0.013699     0.1  0.417493     0.5   
100    0.0  ...  0.431818  0.363290  0.000000    -1.9 -1.369348    -5.0   
101    0.0  ... -0.340909  0.038985 -0.383562    -0.9 -0.132304 

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     0.0   1.25 -0.054348    0.0    0.0  1.662921    0.0   -1.0   -1.0   
91     0.0  -0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
92     1.0   0.00 -0.054348    0.0    0.0  1.370787    0.0   -1.0   -1.0   
93     0.0  -0.50  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
94     0.0   0.00  0.858696    0.0    0.0  0.000000    0.0    0.0    0.0   
95     0.0   1.50  0.239130    0.0    1.0  0.000000    0.0    0.0    0.0   
96     0.0   0.25  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
97     0.0  -0.25  0.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
98     0.0   1.25  1.521739    0.0    0.0  0.000000    0.0    0.0    0.0   
99     0.0   1.00  0.000000    0.0    1.0  0.000000    0.0    0.0    0.0   
100    0.0  -0.75  1.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
101    0.0   1.25  0.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
102    1.0  -0.75 -0.054348    0.0    0.0  1.280899    0.0   -1.0   -1.0   
103    0.0   0.25  1.445652    0.0    1.0  0.000000    0.0    0.0    0.0   
104    1.0   0.25  0.826087    0.0    1.0  0.000000    0.0    0.0    0.0   
105    1.0   1.25  1.793478    0.0    1.0  0.000000    0.0    0.0    0.0   
106    0.0   0.00  1.065217    0.0    0.0  0.000000    0.0    0.0    0.0   
107    0.0  -0.50  0.532609    0.0    0.0  0.000000    0.0    0.0    0.0   
108    1.0  -0.75 -0.054348    0.0    0.0  1.415730    0.0   -1.0   -1.0   
109    1.0   0.75  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
110    1.0  -0.50 -0.054348    0.0    0.0  1.426966    0.0   -1.0   -1.0   
111    0.0   0.00 -0.054348    0.0    0.0  1.404494    0.0   -1.0   -1.0   
112    0.0   0.75 -0.010870    0.0    0.0  0.000000    0.0    0.0    0.0   
113    0.0  -0.50  0.847826    0.0    1.0  0.000000    0.0    0.0    0.0   
114   10.0   0.00 -0.054348    0.0    0.0  0.483146    0.0   -1.0   -1.0   
115    1.0  -0.25  0.673913    0.0    0.0  0.000000    0.0    0.0    0.0   
116    0.0  -0.25 -0.054348    0.0    0.0  1.078652    0.0   -1.0   -1.0   
117    0.0   1.25  1.750000    0.0    0.0  0.000000    0.0    0.0    0.0   
118    1.0   0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
119    0.0   0.00 -0.054348    0.0    0.0  0.977528    0.0   -1.0   -1.0   
120    0.0  -0.75 -0.054348    0.0    0.0  0.123596    0.0   -1.0   -1.0   
121    0.0   1.50 -0.054348    0.0    0.0  1.044944    0.0   -1.0   -1.0   
122    0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
123    0.0   1.50 -0.032609    0.0    1.0  0.000000    0.0    0.0    0.0   
124    0.0   0.25 -0.043478    0.0    1.0  0.000000    0.0    0.0    0.0   
125    0.0   1.00  1.228261    0.0    1.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.50  0.076087    0.0    1.0  0.000000    0.0    0.0    0.0   
127    0.0   1.25 -0.054348    0.0    0.0  1.741573    0.0   -1.0   -1.0   
128    0.0  -0.25  1.597826    0.0    1.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2860    X_2861    X_2862  X_2863    X_2864  X_2865  \
90     0.0  ...  1.227273  1.470690  1.445205    -0.9 -0.334965    -0.5   
91     0.0  ...  0.098485  0.551385  0.698630     0.1  0.650270     4.5   
92     0.0  ...  1.401515  1.701724  1.493151     0.1  0.300163     0.5   
93     0.0  ... -0.174242 -0.090281  0.109589     0.1  0.488434     0.0   
94     0.0  ...  1.204545  1.235909  0.623288     0.0  0.820973     4.5   
95     0.0  ...  0.492424  1.090671  1.342466     0.1 -0.076881     0.0   
96     0.0  ...  0.643939  0.724005  0.506849     0.1  0.406408     0.0   
97     0.0  ...  0.454545  0.215374 -0.410959     0.1  0.508387     0.0   
98     0.0  ... -0.113636 -0.268853 -0.130137    -0.9 -0.271971    -0.5   
99     0.0  ... -0.742424 -0.284329 -0.013699     0.1  0.417493     0.5   
100    0.0  ...  0.431818  0.363290  0.000000    -1.9 -1.369348    -5.0   
101    0.0  ... -0.340909  0.038985 -0.383562    -0.9 -0.132304 

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     0.0   1.25 -0.054348    0.0    0.0  1.662921    0.0   -1.0   -1.0   
91     0.0  -0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
92     1.0   0.00 -0.054348    0.0    0.0  1.370787    0.0   -1.0   -1.0   
93     0.0  -0.50  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
94     0.0   0.00  0.858696    0.0    0.0  0.000000    0.0    0.0    0.0   
95     0.0   1.50  0.239130    0.0    1.0  0.000000    0.0    0.0    0.0   
96     0.0   0.25  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
97     0.0  -0.25  0.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
98     0.0   1.25  1.521739    0.0    0.0  0.000000    0.0    0.0    0.0   
99     0.0   1.00  0.000000    0.0    1.0  0.000000    0.0    0.0    0.0   
100    0.0  -0.75  1.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
101    0.0   1.25  0.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
102    1.0  -0.75 -0.054348    0.0    0.0  1.280899    0.0   -1.0   -1.0   
103    0.0   0.25  1.445652    0.0    1.0  0.000000    0.0    0.0    0.0   
104    1.0   0.25  0.826087    0.0    1.0  0.000000    0.0    0.0    0.0   
105    1.0   1.25  1.793478    0.0    1.0  0.000000    0.0    0.0    0.0   
106    0.0   0.00  1.065217    0.0    0.0  0.000000    0.0    0.0    0.0   
107    0.0  -0.50  0.532609    0.0    0.0  0.000000    0.0    0.0    0.0   
108    1.0  -0.75 -0.054348    0.0    0.0  1.415730    0.0   -1.0   -1.0   
109    1.0   0.75  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
110    1.0  -0.50 -0.054348    0.0    0.0  1.426966    0.0   -1.0   -1.0   
111    0.0   0.00 -0.054348    0.0    0.0  1.404494    0.0   -1.0   -1.0   
112    0.0   0.75 -0.010870    0.0    0.0  0.000000    0.0    0.0    0.0   
113    0.0  -0.50  0.847826    0.0    1.0  0.000000    0.0    0.0    0.0   
114   10.0   0.00 -0.054348    0.0    0.0  0.483146    0.0   -1.0   -1.0   
115    1.0  -0.25  0.673913    0.0    0.0  0.000000    0.0    0.0    0.0   
116    0.0  -0.25 -0.054348    0.0    0.0  1.078652    0.0   -1.0   -1.0   
117    0.0   1.25  1.750000    0.0    0.0  0.000000    0.0    0.0    0.0   
118    1.0   0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
119    0.0   0.00 -0.054348    0.0    0.0  0.977528    0.0   -1.0   -1.0   
120    0.0  -0.75 -0.054348    0.0    0.0  0.123596    0.0   -1.0   -1.0   
121    0.0   1.50 -0.054348    0.0    0.0  1.044944    0.0   -1.0   -1.0   
122    0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
123    0.0   1.50 -0.032609    0.0    1.0  0.000000    0.0    0.0    0.0   
124    0.0   0.25 -0.043478    0.0    1.0  0.000000    0.0    0.0    0.0   
125    0.0   1.00  1.228261    0.0    1.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.50  0.076087    0.0    1.0  0.000000    0.0    0.0    0.0   
127    0.0   1.25 -0.054348    0.0    0.0  1.741573    0.0   -1.0   -1.0   
128    0.0  -0.25  1.597826    0.0    1.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2860    X_2861    X_2862  X_2863    X_2864  X_2865  \
90     0.0  ...  1.227273  1.470690  1.445205    -0.9 -0.334965    -0.5   
91     0.0  ...  0.098485  0.551385  0.698630     0.1  0.650270     4.5   
92     0.0  ...  1.401515  1.701724  1.493151     0.1  0.300163     0.5   
93     0.0  ... -0.174242 -0.090281  0.109589     0.1  0.488434     0.0   
94     0.0  ...  1.204545  1.235909  0.623288     0.0  0.820973     4.5   
95     0.0  ...  0.492424  1.090671  1.342466     0.1 -0.076881     0.0   
96     0.0  ...  0.643939  0.724005  0.506849     0.1  0.406408     0.0   
97     0.0  ...  0.454545  0.215374 -0.410959     0.1  0.508387     0.0   
98     0.0  ... -0.113636 -0.268853 -0.130137    -0.9 -0.271971    -0.5   
99     0.0  ... -0.742424 -0.284329 -0.013699     0.1  0.417493     0.5   
100    0.0  ...  0.431818  0.363290  0.000000    -1.9 -1.369348    -5.0   
101    0.0  ... -0.340909  0.038985 -0.383562    -0.9 -0.132304 

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     0.0   1.25 -0.054348    0.0    0.0  1.662921    0.0   -1.0   -1.0   
91     0.0  -0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
92     1.0   0.00 -0.054348    0.0    0.0  1.370787    0.0   -1.0   -1.0   
93     0.0  -0.50  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
94     0.0   0.00  0.858696    0.0    0.0  0.000000    0.0    0.0    0.0   
95     0.0   1.50  0.239130    0.0    1.0  0.000000    0.0    0.0    0.0   
96     0.0   0.25  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
97     0.0  -0.25  0.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
98     0.0   1.25  1.521739    0.0    0.0  0.000000    0.0    0.0    0.0   
99     0.0   1.00  0.000000    0.0    1.0  0.000000    0.0    0.0    0.0   
100    0.0  -0.75  1.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
101    0.0   1.25  0.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
102    1.0  -0.75 -0.054348    0.0    0.0  1.280899    0.0   -1.0   -1.0   
103    0.0   0.25  1.445652    0.0    1.0  0.000000    0.0    0.0    0.0   
104    1.0   0.25  0.826087    0.0    1.0  0.000000    0.0    0.0    0.0   
105    1.0   1.25  1.793478    0.0    1.0  0.000000    0.0    0.0    0.0   
106    0.0   0.00  1.065217    0.0    0.0  0.000000    0.0    0.0    0.0   
107    0.0  -0.50  0.532609    0.0    0.0  0.000000    0.0    0.0    0.0   
108    1.0  -0.75 -0.054348    0.0    0.0  1.415730    0.0   -1.0   -1.0   
109    1.0   0.75  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
110    1.0  -0.50 -0.054348    0.0    0.0  1.426966    0.0   -1.0   -1.0   
111    0.0   0.00 -0.054348    0.0    0.0  1.404494    0.0   -1.0   -1.0   
112    0.0   0.75 -0.010870    0.0    0.0  0.000000    0.0    0.0    0.0   
113    0.0  -0.50  0.847826    0.0    1.0  0.000000    0.0    0.0    0.0   
114   10.0   0.00 -0.054348    0.0    0.0  0.483146    0.0   -1.0   -1.0   
115    1.0  -0.25  0.673913    0.0    0.0  0.000000    0.0    0.0    0.0   
116    0.0  -0.25 -0.054348    0.0    0.0  1.078652    0.0   -1.0   -1.0   
117    0.0   1.25  1.750000    0.0    0.0  0.000000    0.0    0.0    0.0   
118    1.0   0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
119    0.0   0.00 -0.054348    0.0    0.0  0.977528    0.0   -1.0   -1.0   
120    0.0  -0.75 -0.054348    0.0    0.0  0.123596    0.0   -1.0   -1.0   
121    0.0   1.50 -0.054348    0.0    0.0  1.044944    0.0   -1.0   -1.0   
122    0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
123    0.0   1.50 -0.032609    0.0    1.0  0.000000    0.0    0.0    0.0   
124    0.0   0.25 -0.043478    0.0    1.0  0.000000    0.0    0.0    0.0   
125    0.0   1.00  1.228261    0.0    1.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.50  0.076087    0.0    1.0  0.000000    0.0    0.0    0.0   
127    0.0   1.25 -0.054348    0.0    0.0  1.741573    0.0   -1.0   -1.0   
128    0.0  -0.25  1.597826    0.0    1.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2860    X_2861    X_2862  X_2863    X_2864  X_2865  \
90     0.0  ...  1.227273  1.470690  1.445205    -0.9 -0.334965    -0.5   
91     0.0  ...  0.098485  0.551385  0.698630     0.1  0.650270     4.5   
92     0.0  ...  1.401515  1.701724  1.493151     0.1  0.300163     0.5   
93     0.0  ... -0.174242 -0.090281  0.109589     0.1  0.488434     0.0   
94     0.0  ...  1.204545  1.235909  0.623288     0.0  0.820973     4.5   
95     0.0  ...  0.492424  1.090671  1.342466     0.1 -0.076881     0.0   
96     0.0  ...  0.643939  0.724005  0.506849     0.1  0.406408     0.0   
97     0.0  ...  0.454545  0.215374 -0.410959     0.1  0.508387     0.0   
98     0.0  ... -0.113636 -0.268853 -0.130137    -0.9 -0.271971    -0.5   
99     0.0  ... -0.742424 -0.284329 -0.013699     0.1  0.417493     0.5   
100    0.0  ...  0.431818  0.363290  0.000000    -1.9 -1.369348    -5.0   
101    0.0  ... -0.340909  0.038985 -0.383562    -0.9 -0.132304 

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     0.0   1.25 -0.054348    0.0    0.0  1.662921    0.0   -1.0   -1.0   
91     0.0  -0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
92     1.0   0.00 -0.054348    0.0    0.0  1.370787    0.0   -1.0   -1.0   
93     0.0  -0.50  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
94     0.0   0.00  0.858696    0.0    0.0  0.000000    0.0    0.0    0.0   
95     0.0   1.50  0.239130    0.0    1.0  0.000000    0.0    0.0    0.0   
96     0.0   0.25  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
97     0.0  -0.25  0.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
98     0.0   1.25  1.521739    0.0    0.0  0.000000    0.0    0.0    0.0   
99     0.0   1.00  0.000000    0.0    1.0  0.000000    0.0    0.0    0.0   
100    0.0  -0.75  1.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
101    0.0   1.25  0.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
102    1.0  -0.75 -0.054348    0.0    0.0  1.280899    0.0   -1.0   -1.0   
103    0.0   0.25  1.445652    0.0    1.0  0.000000    0.0    0.0    0.0   
104    1.0   0.25  0.826087    0.0    1.0  0.000000    0.0    0.0    0.0   
105    1.0   1.25  1.793478    0.0    1.0  0.000000    0.0    0.0    0.0   
106    0.0   0.00  1.065217    0.0    0.0  0.000000    0.0    0.0    0.0   
107    0.0  -0.50  0.532609    0.0    0.0  0.000000    0.0    0.0    0.0   
108    1.0  -0.75 -0.054348    0.0    0.0  1.415730    0.0   -1.0   -1.0   
109    1.0   0.75  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
110    1.0  -0.50 -0.054348    0.0    0.0  1.426966    0.0   -1.0   -1.0   
111    0.0   0.00 -0.054348    0.0    0.0  1.404494    0.0   -1.0   -1.0   
112    0.0   0.75 -0.010870    0.0    0.0  0.000000    0.0    0.0    0.0   
113    0.0  -0.50  0.847826    0.0    1.0  0.000000    0.0    0.0    0.0   
114   10.0   0.00 -0.054348    0.0    0.0  0.483146    0.0   -1.0   -1.0   
115    1.0  -0.25  0.673913    0.0    0.0  0.000000    0.0    0.0    0.0   
116    0.0  -0.25 -0.054348    0.0    0.0  1.078652    0.0   -1.0   -1.0   
117    0.0   1.25  1.750000    0.0    0.0  0.000000    0.0    0.0    0.0   
118    1.0   0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
119    0.0   0.00 -0.054348    0.0    0.0  0.977528    0.0   -1.0   -1.0   
120    0.0  -0.75 -0.054348    0.0    0.0  0.123596    0.0   -1.0   -1.0   
121    0.0   1.50 -0.054348    0.0    0.0  1.044944    0.0   -1.0   -1.0   
122    0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
123    0.0   1.50 -0.032609    0.0    1.0  0.000000    0.0    0.0    0.0   
124    0.0   0.25 -0.043478    0.0    1.0  0.000000    0.0    0.0    0.0   
125    0.0   1.00  1.228261    0.0    1.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.50  0.076087    0.0    1.0  0.000000    0.0    0.0    0.0   
127    0.0   1.25 -0.054348    0.0    0.0  1.741573    0.0   -1.0   -1.0   
128    0.0  -0.25  1.597826    0.0    1.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2860    X_2861    X_2862  X_2863    X_2864  X_2865  \
90     0.0  ...  1.227273  1.470690  1.445205    -0.9 -0.334965    -0.5   
91     0.0  ...  0.098485  0.551385  0.698630     0.1  0.650270     4.5   
92     0.0  ...  1.401515  1.701724  1.493151     0.1  0.300163     0.5   
93     0.0  ... -0.174242 -0.090281  0.109589     0.1  0.488434     0.0   
94     0.0  ...  1.204545  1.235909  0.623288     0.0  0.820973     4.5   
95     0.0  ...  0.492424  1.090671  1.342466     0.1 -0.076881     0.0   
96     0.0  ...  0.643939  0.724005  0.506849     0.1  0.406408     0.0   
97     0.0  ...  0.454545  0.215374 -0.410959     0.1  0.508387     0.0   
98     0.0  ... -0.113636 -0.268853 -0.130137    -0.9 -0.271971    -0.5   
99     0.0  ... -0.742424 -0.284329 -0.013699     0.1  0.417493     0.5   
100    0.0  ...  0.431818  0.363290  0.000000    -1.9 -1.369348    -5.0   
101    0.0  ... -0.340909  0.038985 -0.383562    -0.9 -0.132304 

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
90     0.0   1.25 -0.054348    0.0    0.0  1.662921    0.0   -1.0   -1.0   
91     0.0  -0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
92     1.0   0.00 -0.054348    0.0    0.0  1.370787    0.0   -1.0   -1.0   
93     0.0  -0.50  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
94     0.0   0.00  0.858696    0.0    0.0  0.000000    0.0    0.0    0.0   
95     0.0   1.50  0.239130    0.0    1.0  0.000000    0.0    0.0    0.0   
96     0.0   0.25  0.217391    0.0    1.0  0.000000    0.0    0.0    0.0   
97     0.0  -0.25  0.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
98     0.0   1.25  1.521739    0.0    0.0  0.000000    0.0    0.0    0.0   
99     0.0   1.00  0.000000    0.0    1.0  0.000000    0.0    0.0    0.0   
100    0.0  -0.75  1.510870    0.0    1.0  0.000000    0.0    0.0    0.0   
101    0.0   1.25  0.663043    0.0    0.0  0.000000    0.0    0.0    0.0   
102    1.0  -0.75 -0.054348    0.0    0.0  1.280899    0.0   -1.0   -1.0   
103    0.0   0.25  1.445652    0.0    1.0  0.000000    0.0    0.0    0.0   
104    1.0   0.25  0.826087    0.0    1.0  0.000000    0.0    0.0    0.0   
105    1.0   1.25  1.793478    0.0    1.0  0.000000    0.0    0.0    0.0   
106    0.0   0.00  1.065217    0.0    0.0  0.000000    0.0    0.0    0.0   
107    0.0  -0.50  0.532609    0.0    0.0  0.000000    0.0    0.0    0.0   
108    1.0  -0.75 -0.054348    0.0    0.0  1.415730    0.0   -1.0   -1.0   
109    1.0   0.75  1.793478    0.0    0.0  0.000000    0.0    0.0    0.0   
110    1.0  -0.50 -0.054348    0.0    0.0  1.426966    0.0   -1.0   -1.0   
111    0.0   0.00 -0.054348    0.0    0.0  1.404494    0.0   -1.0   -1.0   
112    0.0   0.75 -0.010870    0.0    0.0  0.000000    0.0    0.0    0.0   
113    0.0  -0.50  0.847826    0.0    1.0  0.000000    0.0    0.0    0.0   
114   10.0   0.00 -0.054348    0.0    0.0  0.483146    0.0   -1.0   -1.0   
115    1.0  -0.25  0.673913    0.0    0.0  0.000000    0.0    0.0    0.0   
116    0.0  -0.25 -0.054348    0.0    0.0  1.078652    0.0   -1.0   -1.0   
117    0.0   1.25  1.750000    0.0    0.0  0.000000    0.0    0.0    0.0   
118    1.0   0.25 -0.054348    0.0    0.0  1.449438    0.0   -1.0   -1.0   
119    0.0   0.00 -0.054348    0.0    0.0  0.977528    0.0   -1.0   -1.0   
120    0.0  -0.75 -0.054348    0.0    0.0  0.123596    0.0   -1.0   -1.0   
121    0.0   1.50 -0.054348    0.0    0.0  1.044944    0.0   -1.0   -1.0   
122    0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
123    0.0   1.50 -0.032609    0.0    1.0  0.000000    0.0    0.0    0.0   
124    0.0   0.25 -0.043478    0.0    1.0  0.000000    0.0    0.0    0.0   
125    0.0   1.00  1.228261    0.0    1.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.50  0.076087    0.0    1.0  0.000000    0.0    0.0    0.0   
127    0.0   1.25 -0.054348    0.0    0.0  1.741573    0.0   -1.0   -1.0   
128    0.0  -0.25  1.597826    0.0    1.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2860    X_2861    X_2862  X_2863    X_2864  X_2865  \
90     0.0  ...  1.227273  1.470690  1.445205    -0.9 -0.334965    -0.5   
91     0.0  ...  0.098485  0.551385  0.698630     0.1  0.650270     4.5   
92     0.0  ...  1.401515  1.701724  1.493151     0.1  0.300163     0.5   
93     0.0  ... -0.174242 -0.090281  0.109589     0.1  0.488434     0.0   
94     0.0  ...  1.204545  1.235909  0.623288     0.0  0.820973     4.5   
95     0.0  ...  0.492424  1.090671  1.342466     0.1 -0.076881     0.0   
96     0.0  ...  0.643939  0.724005  0.506849     0.1  0.406408     0.0   
97     0.0  ...  0.454545  0.215374 -0.410959     0.1  0.508387     0.0   
98     0.0  ... -0.113636 -0.268853 -0.130137    -0.9 -0.271971    -0.5   
99     0.0  ... -0.742424 -0.284329 -0.013699     0.1  0.417493     0.5   
100    0.0  ...  0.431818  0.363290  0.000000    -1.9 -1.369348    -5.0   
101    0.0  ... -0.340909  0.038985 -0.383562    -0.9 -0.132304 

In [85]:
T01_final_regression_model = finalize_model(T01_model_et)

In [86]:
T01_prediction = predict_model(T01_final_regression_model, data=T01_data)

In [87]:
T01_datas = T01_prediction['prediction_label']
T01_datas = pd.DataFrame(T01_datas.values, columns = ['Y_Quality'])
T01_datas

Y_Quality
0     0.521249
1     0.524408
2     0.523714
3     0.521083
4     0.518024
..         ...
124   0.535279
125   0.535589
126   0.553733
127   0.554562
128   0.560317

[129 rows x 1 columns]

In [88]:
T01y_idx= T01_class.index
T01y_idx = pd.DataFrame(T01y_idx, columns = ['index'])
T01_datas = pd.concat([T01y_idx, T01_datas], axis = 1)
T01_datas = T01_datas.set_index('index')
T01_datas

Y_Quality
index           
28      0.521249
66      0.524408
116     0.523714
118     0.521083
123     0.518024
...          ...
293     0.535279
419     0.535589
471     0.553733
472     0.554562
531     0.560317

[129 rows x 1 columns]

In [89]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T01_datas, 
                   target=T01_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [90]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbc = create_model('gbc', fold = 5)
T01_total_models.append(T01_model_gbc)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [91]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbc = tune_model(T01_model_gbc, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [92]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbc, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]
T01_tuned_models

[LGBMClassifier(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
                importance_type='split', learning_rate=0.1, max_depth=-1,
                min_child_samples=20, min_child_weight=0.001, min_split_gain=0.0,
                n_estimators=100, n_jobs=-1, num_leaves=31, objective=None,
                random_state=414, reg_alpha=0.0, reg_lambda=0.0, silent=True,
                subsample=1.0, subsample_for_bin=200000, subsample_freq=0),
 RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                        criterion='gini', max_depth=None, max_features='auto',
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.0, min_samples_leaf=1,
                        min_samples_split=2, min_weight_fraction_leaf=0.0,
                        n_estimators=100, n_jobs=-1, oob_score=False,
                        random_state=414, verbose=0, warm_start=False),
 GradientBoostingClassifier(ccp

In [93]:
for model in T01_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531970        1                 1            0.9992
91    0.517938        0                 0            0.9912
92    0.524408        0                 0            0.9912
93    0.523694        0                 0            0.9912
94    0.527486        1                 1            0.9992
95    0.524487        0                 0            0.9912
96    0.530568        1                 1            0.9992
97    0.560317        2                 2            0.9999
98    0.535394        2                 2            0.9999
99    0.549381        2                 2            0.9999
100   0.528687        1                 1            0.9992
101   0.544089        2                 2            0.9999
102   0.547492        2                 2            0.9999
103   0.529171        1                 1            0.9992
104   0.547516        2                 2            0.9999
105   0.533273        1                 1            0.9992
106   0.533122        1                 1            0.9992
107   0.528190        1                 1            0.9992
108   0.531522        1                 1            0.9992
109   0.518024        0                 0            0.9912
110   0.528270        1                 1            0.9992
111   0.536951        2                 2            0.9999
112   0.531043        1                 1            0.9992
113   0.534403        1                 1            0.9992
114   0.535589        2                 2            0.9999
115   0.538502        2                 2            0.9999
116   0.530048        1                 1            0.9992
117   0.534486        1                 1            0.9992
118   0.528087        1                 1            0.9992
119   0.526906        1                 1            0.9955
120   0.525221        1                 1            0.6632
121   0.527735        1                 1            0.9992
122   0.531583        1                 1            0.9992
123   0.530022        1                 1            0.9992
124   0.527689        1                 1            0.9992
125   0.533179        1                 1            0.9992
126   0.537116        2                 2            0.9999
127   0.523714        0                 0            0.9912
128   0.538614        2                 2            0.9999

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531970        1                 1              1.00
91    0.517938        0                 0              1.00
92    0.524408        0                 0              0.98
93    0.523694        0                 0              0.99
94    0.527486        1                 1              1.00
95    0.524487        0                 0              0.98
96    0.530568        1                 1              1.00
97    0.560317        2                 2              1.00
98    0.535394        2                 2              0.96
99    0.549381        2                 2              1.00
100   0.528687        1                 1              1.00
101   0.544089        2                 2              1.00
102   0.547492        2                 2              1.00
103   0.529171        1                 1              1.00
104   0.547516        2                 2              1.00
105   0.533273        1                 1              1.00
106   0.533122        1                 1              1.00
107   0.528190        1                 1              1.00
108   0.531522        1                 1              1.00
109   0.518024        0                 0              1.00
110   0.528270        1                 1              1.00
111   0.536951        2                 2              1.00
112   0.531043        1                 1              1.00
113   0.534403        1                 1              1.00
114   0.535589        2                 2              1.00
115   0.538502        2                 2              1.00
116   0.530048        1                 1              1.00
117   0.534486        1                 1              1.00
118   0.528087        1                 1              1.00
119   0.526906        1                 1              1.00
120   0.525221        1                 0              0.83
121   0.527735        1                 1              1.00
122   0.531583        1                 1              1.00
123   0.530022        1                 1              1.00
124   0.527689        1                 1              1.00
125   0.533179        1                 1              1.00
126   0.537116        2                 2              1.00
127   0.523714        0                 0              0.99
128   0.538614        2                 2              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531970        1                 1               1.0
91    0.517938        0                 0               1.0
92    0.524408        0                 0               1.0
93    0.523694        0                 0               1.0
94    0.527486        1                 1               1.0
95    0.524487        0                 0               1.0
96    0.530568        1                 1               1.0
97    0.560317        2                 2               1.0
98    0.535394        2                 2               1.0
99    0.549381        2                 2               1.0
100   0.528687        1                 1               1.0
101   0.544089        2                 2               1.0
102   0.547492        2                 2               1.0
103   0.529171        1                 1               1.0
104   0.547516        2                 2               1.0
105   0.533273        1                 1               1.0
106   0.533122        1                 1               1.0
107   0.528190        1                 1               1.0
108   0.531522        1                 1               1.0
109   0.518024        0                 0               1.0
110   0.528270        1                 1               1.0
111   0.536951        2                 2               1.0
112   0.531043        1                 1               1.0
113   0.534403        1                 1               1.0
114   0.535589        2                 2               1.0
115   0.538502        2                 2               1.0
116   0.530048        1                 1               1.0
117   0.534486        1                 1               1.0
118   0.528087        1                 1               1.0
119   0.526906        1                 1               1.0
120   0.525221        1                 0               1.0
121   0.527735        1                 1               1.0
122   0.531583        1                 1               1.0
123   0.530022        1                 1               1.0
124   0.527689        1                 1               1.0
125   0.533179        1                 1               1.0
126   0.537116        2                 2               1.0
127   0.523714        0                 0               1.0
128   0.538614        2                 2               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531970        1                 1               1.0
91    0.517938        0                 0               1.0
92    0.524408        0                 0               1.0
93    0.523694        0                 0               1.0
94    0.527486        1                 1               1.0
95    0.524487        0                 0               1.0
96    0.530568        1                 1               1.0
97    0.560317        2                 2               1.0
98    0.535394        2                 2               1.0
99    0.549381        2                 2               1.0
100   0.528687        1                 1               1.0
101   0.544089        2                 2               1.0
102   0.547492        2                 2               1.0
103   0.529171        1                 1               1.0
104   0.547516        2                 2               1.0
105   0.533273        1                 1               1.0
106   0.533122        1                 1               1.0
107   0.528190        1                 1               1.0
108   0.531522        1                 1               1.0
109   0.518024        0                 0               1.0
110   0.528270        1                 1               1.0
111   0.536951        2                 2               1.0
112   0.531043        1                 1               1.0
113   0.534403        1                 1               1.0
114   0.535589        2                 2               1.0
115   0.538502        2                 2               1.0
116   0.530048        1                 1               1.0
117   0.534486        1                 1               1.0
118   0.528087        1                 1               1.0
119   0.526906        1                 1               1.0
120   0.525221        1                 0               0.6
121   0.527735        1                 1               1.0
122   0.531583        1                 1               1.0
123   0.530022        1                 1               1.0
124   0.527689        1                 1               1.0
125   0.533179        1                 1               1.0
126   0.537116        2                 2               1.0
127   0.523714        0                 0               1.0
128   0.538614        2                 2               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531970        1                 1            0.9996
91    0.517938        0                 0            0.9973
92    0.524408        0                 0            0.9967
93    0.523694        0                 0            0.9972
94    0.527486        1                 1            0.9994
95    0.524487        0                 0            0.9944
96    0.530568        1                 1            0.9996
97    0.560317        2                 2            0.9982
98    0.535394        2                 2            0.9949
99    0.549381        2                 2            0.9989
100   0.528687        1                 1            0.9994
101   0.544089        2                 2            0.9991
102   0.547492        2                 2            0.9990
103   0.529171        1                 1            0.9995
104   0.547516        2                 2            0.9990
105   0.533273        1                 1            0.9995
106   0.533122        1                 1            0.9995
107   0.528190        1                 1            0.9994
108   0.531522        1                 1            0.9996
109   0.518024        0                 0            0.9973
110   0.528270        1                 1            0.9994
111   0.536951        2                 2            0.9989
112   0.531043        1                 1            0.9996
113   0.534403        1                 1            0.9991
114   0.535589        2                 2            0.9949
115   0.538502        2                 2            0.9991
116   0.530048        1                 1            0.9996
117   0.534486        1                 1            0.9987
118   0.528087        1                 1            0.9994
119   0.526906        1                 1            0.9994
120   0.525221        1                 0            0.9791
121   0.527735        1                 1            0.9994
122   0.531583        1                 1            0.9996
123   0.530022        1                 1            0.9996
124   0.527689        1                 1            0.9994
125   0.533179        1                 1            0.9995
126   0.537116        2                 2            0.9989
127   0.523714        0                 0            0.9972
128   0.538614        2                 2            0.9991

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531970        1                 1            0.9953
91    0.517938        0                 0            0.9665
92    0.524408        0                 0            0.9665
93    0.523694        0                 0            0.9665
94    0.527486        1                 1            0.9849
95    0.524487        0                 0            0.9665
96    0.530568        1                 1            0.9953
97    0.560317        2                 2            0.9836
98    0.535394        2                 2            0.9836
99    0.549381        2                 2            0.9836
100   0.528687        1                 1            0.9949
101   0.544089        2                 2            0.9836
102   0.547492        2                 2            0.9836
103   0.529171        1                 1            0.9953
104   0.547516        2                 2            0.9836
105   0.533273        1                 1            0.9872
106   0.533122        1                 1            0.9879
107   0.528190        1                 1            0.9904
108   0.531522        1                 1            0.9953
109   0.518024        0                 0            0.9665
110   0.528270        1                 1            0.9904
111   0.536951        2                 2            0.9836
112   0.531043        1                 1            0.9953
113   0.534403        1                 1            0.9840
114   0.535589        2                 2            0.9836
115   0.538502        2                 2            0.9836
116   0.530048        1                 1            0.9953
117   0.534486        1                 1            0.9840
118   0.528087        1                 1            0.9904
119   0.526906        1                 1            0.9833
120   0.525221        1                 0            0.9665
121   0.527735        1                 1            0.9904
122   0.531583        1                 1            0.9953
123   0.530022        1                 1            0.9953
124   0.527689        1                 1            0.9904
125   0.533179        1                 1            0.9872
126   0.537116        2                 2            0.9836
127   0.523714        0                 0            0.9665
128   0.538614        2                 2            0.9836

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531970        1                 1               1.0
91    0.517938        0                 0               1.0
92    0.524408        0                 0               1.0
93    0.523694        0                 0               1.0
94    0.527486        1                 1               1.0
95    0.524487        0                 0               1.0
96    0.530568        1                 1               1.0
97    0.560317        2                 2               1.0
98    0.535394        2                 2               1.0
99    0.549381        2                 2               1.0
100   0.528687        1                 1               1.0
101   0.544089        2                 2               1.0
102   0.547492        2                 2               1.0
103   0.529171        1                 1               1.0
104   0.547516        2                 2               1.0
105   0.533273        1                 1               1.0
106   0.533122        1                 1               1.0
107   0.528190        1                 1               1.0
108   0.531522        1                 1               1.0
109   0.518024        0                 0               1.0
110   0.528270        1                 1               1.0
111   0.536951        2                 2               1.0
112   0.531043        1                 1               1.0
113   0.534403        1                 1               1.0
114   0.535589        2                 2               1.0
115   0.538502        2                 2               1.0
116   0.530048        1                 1               1.0
117   0.534486        1                 1               1.0
118   0.528087        1                 1               1.0
119   0.526906        1                 1               1.0
120   0.525221        1                 0               1.0
121   0.527735        1                 1               1.0
122   0.531583        1                 1               1.0
123   0.530022        1                 1               1.0
124   0.527689        1                 1               1.0
125   0.533179        1                 1               1.0
126   0.537116        2                 2               1.0
127   0.523714        0                 0               1.0
128   0.538614        2                 2               1.0

In [94]:
T01_final_classification_model = finalize_model(T01_model_gbc)

In [95]:
T01_prediction = predict_model(T01_final_classification_model, data=T01_datas)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [96]:
T01_y_class = pd.DataFrame(T01_class, columns = ['Y_Class'])
T01_idx = T01_y_class.index
T01_y_class = T01_y_class.reset_index()
T01_prediction = pd.concat([T01_prediction, T01_y_class], axis = 1)
T01_prediction = T01_prediction.set_index('index')
T01_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [97]:
T01_prediction

Y_Quality  prediction_label  prediction_score
index                                               
28      0.521249                 0               1.0
66      0.524408                 0               1.0
116     0.523714                 0               1.0
118     0.521083                 0               1.0
123     0.518024                 0               1.0
...          ...               ...               ...
293     0.535279                 2               1.0
419     0.535589                 2               1.0
471     0.553733                 2               1.0
472     0.554562                 2               1.0
531     0.560317                 2               1.0

[129 rows x 3 columns]

# T10

In [98]:
T10_class = T10['Y_Class']
T10_target = T10['Y_Quality']
T10_data = T10.drop(['Y_Class', 'Y_Quality'], axis = 1)
T10_data

X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  X_10  ...  \
22   2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
23   2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
85   2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
86   2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
87   2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
..   ...    ...  ...   ...   ...  ...   ...   ...   ...   ...  ...   
512  2.0   89.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0   2.0  ...   
516  2.0   89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  ...   
570  6.0   90.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0   2.0  ...   
572  6.0   89.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0   2.0  ...   
578  2.0   91.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0   2.0  ...   

          X_926       X_927       X_928       X_929       X_930     X_931  \
22   157.235484  150.900000  326.000000  309.290909  290.000000  13.70000   
23   154.500485  147.962963  323.074074  307.664743  292.074074  13.67037   
85   153.870968  151.100000  326.000000  313.181818  298.000000  13.70000   
86   157.283871  154.000000  327.000000  313.981818  299.000000  13.60000   
87   155.270000  151.300000  327.000000  311.763636  298.000000  13.70000   
..          ...         ...         ...         ...         ...       ...   
512  152.700000  141.000000  327.000000  307.672727  290.000000  13.60000   
516  153.267742  148.300000  326.000000  313.236364  298.000000  13.60000   
570  157.464516  154.500000  327.000000  312.454545  298.000000  13.70000   
572  161.046667  151.300000  326.000000  312.537037  298.000000  13.70000   
578  157.541935  150.400000  320.000000  303.727273  289.000000  13.60000   

         X_932     X_933  HOUR  DAY_OF_WEEK  
22   13.443333  13.20000     8            2  
23   13.448694  13.22963     9            2  
85   13.480645  13.20000    19            5  
86   13.425806  13.20000    20            5  
87   13.512903  13.30000    20            5  
..         ...       ...   ...          ...  
512  13.383333  13.20000    21            6  
516  13.376667  13.20000     2            7  
570  13.454839  13.30000    18            6  
572  13.440000  13.20000    18            6  
578  13.354839  13.20000     0            7  

[349 rows x 667 columns]

In [99]:
T_10c = T10_data.columns
T_10scaler = RobustScaler()
T_10scaled = T_10scaler.fit_transform(T10_data)
T10_data = pd.DataFrame(T_10scaled, columns = T_10c)
T10_data

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...     X_926  \
0    0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.947697   
1    0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.134022   
2    0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -0.053263   
3    0.0  0.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.962092   
4    0.0  1.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.362956   
..   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...       ...   
344  0.0 -1.2  0.0  0.0  0.0  0.0  2.000000  0.0  1.0   0.0  ... -0.401631   
345  0.0 -1.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ... -0.232726   
346  4.0 -1.0  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...  1.015835   
347  4.0 -1.2  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...  2.081542   
348  0.0 -0.8  0.0  0.0  0.0  0.0  2.000000  0.0  1.0   0.0  ...  1.038868   

        X_927     X_928     X_929     X_930     X_931     X_932    X_933  \
0    0.660000  0.000000  0.373576  0.111111  1.000000  0.584058  0.00000   
1    0.072593 -0.292593  0.169842  0.341564  0.703704  0.656307  0.02963   
2    0.700000  0.000000  0.861048  1.000000  1.000000  1.086956  0.00000   
3    1.280000  0.100000  0.961276  1.111111  0.000000  0.347826  0.00000   
4    0.740000  0.100000  0.683371  1.000000  1.000000  1.521739  0.10000   
..        ...       ...       ...       ...       ...       ...      ...   
344 -1.320000  0.100000  0.170843  0.111111  0.000000 -0.224638  0.00000   
345  0.140000  0.000000  0.867882  1.000000  0.000000 -0.314493  0.00000   
346  1.380000  0.100000  0.769932  1.000000  1.000000  0.739130  0.10000   
347  0.740000  0.000000  0.780267  1.000000  1.000000  0.539130  0.00000   
348  0.560000 -0.600000 -0.323462  0.000000  0.000000 -0.608696  0.00000   

         HOUR  DAY_OF_WEEK  
0   -0.166667    -1.000000  
1   -0.083333    -1.000000  
2    0.750000     0.000000  
3    0.833333     0.000000  
4    0.833333     0.000000  
..        ...          ...  
344  0.916667     0.333333  
345 -0.666667     0.666667  
346  0.666667     0.333333  
347  0.666667     0.333333  
348 -0.833333     0.666667  

[349 rows x 667 columns]

In [100]:
T10_y_class = pd.DataFrame(T10_target, columns = ['Y_Quality'])
T10_idx = T10_y_class.index
T10_y_class = T10_y_class.reset_index()
T10_data = pd.concat([T10_data, T10_y_class], axis = 1)
T10_data = T10_data.set_index('index')
T10_data.drop(['Y_Quality'], axis = 1, inplace = True)
T10_data

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...     X_926  \
index                                                          ...             
22     0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.947697   
23     0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.134022   
85     0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -0.053263   
86     0.0  0.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.962092   
87     0.0  1.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  0.362956   
...    ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...       ...   
512    0.0 -1.2  0.0  0.0  0.0  0.0  2.000000  0.0  1.0   0.0  ... -0.401631   
516    0.0 -1.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ... -0.232726   
570    4.0 -1.0  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...  1.015835   
572    4.0 -1.2  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...  2.081542   
578    0.0 -0.8  0.0  0.0  0.0  0.0  2.000000  0.0  1.0   0.0  ...  1.038868   

          X_927     X_928     X_929     X_930     X_931     X_932    X_933  \
index                                                                        
22     0.660000  0.000000  0.373576  0.111111  1.000000  0.584058  0.00000   
23     0.072593 -0.292593  0.169842  0.341564  0.703704  0.656307  0.02963   
85     0.700000  0.000000  0.861048  1.000000  1.000000  1.086956  0.00000   
86     1.280000  0.100000  0.961276  1.111111  0.000000  0.347826  0.00000   
87     0.740000  0.100000  0.683371  1.000000  1.000000  1.521739  0.10000   
...         ...       ...       ...       ...       ...       ...      ...   
512   -1.320000  0.100000  0.170843  0.111111  0.000000 -0.224638  0.00000   
516    0.140000  0.000000  0.867882  1.000000  0.000000 -0.314493  0.00000   
570    1.380000  0.100000  0.769932  1.000000  1.000000  0.739130  0.10000   
572    0.740000  0.000000  0.780267  1.000000  1.000000  0.539130  0.00000   
578    0.560000 -0.600000 -0.323462  0.000000  0.000000 -0.608696  0.00000   

           HOUR  DAY_OF_WEEK  
index                         
22    -0.166667    -1.000000  
23    -0.083333    -1.000000  
85     0.750000     0.000000  
86     0.833333     0.000000  
87     0.833333     0.000000  
...         ...          ...  
512    0.916667     0.333333  
516   -0.666667     0.666667  
570    0.666667     0.333333  
572    0.666667     0.333333  
578   -0.833333     0.666667  

[349 rows x 667 columns]

In [101]:
#13
from pycaret.regression import *
setup_rgs = setup(data = T10_data, target = T10_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [102]:
T10_total_models = []

T10_model_rf = create_model('rf', fold = 5)
T10_total_models.append(T10_model_rf)

T10_model_gbr = create_model('gbr', fold = 5)
T10_total_models.append(T10_model_gbr)

T10_model_et = create_model('et', fold = 5)
T10_total_models.append(T10_model_et)

T10_model_catboost = create_model('catboost', fold = 5)
T10_total_models.append(T10_model_catboost)

T10_model_xgb = create_model('xgboost', fold = 5)
T10_total_models.append(T10_model_xgb)

T10_model_ada = create_model('ada', fold = 5)
T10_total_models.append(T10_model_ada)

T10_model_lightgbm = create_model('lightgbm', fold = 5)
T10_total_models.append(T10_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [103]:
T10_model_rf = tune_model(T10_model_rf, fold=5, choose_better = True)

T10_model_gbr = tune_model(T10_model_gbr, fold=5, choose_better = True)

T10_model_et = tune_model(T10_model_et, fold=5, choose_better = True)

T10_model_catboost = tune_model(T10_model_catboost, fold=5, choose_better = True)

T10_model_xgb = tune_model(T10_model_xgb, fold=5, choose_better = True)

T10_model_ada = tune_model(T10_model_ada, fold=5, choose_better = True)

T10_model_lightgbm = tune_model(T10_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [104]:
T10_tuned_models = [T10_model_rf, T10_model_gbr, T10_model_et, T10_model_catboost, T10_model_xgb, T10_model_ada, T10_model_lightgbm]
T10_tuned_models

[RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='squared_error',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       max_samples=None, min_impurity_decrease=0.0,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=-1,
                       oob_score=False, random_state=414, verbose=0,
                       warm_start=False),
 GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0, criterion='friedman_mse',
                           init=None, learning_rate=0.15, loss='squared_error',
                           max_depth=8, max_features='sqrt', max_leaf_nodes=None,
                           min_impurity_decrease=0.0001, min_samples_leaf=2,
                           min_samples_split=4, min_weight_fraction_leaf=0.0,
                           n_estimators=210, n_iter_no_change=None,
                           random_state=414, subs

In [105]:
for model in T10_tuned_models:
    display(predict_model(model))

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  X_928  \
244  0.0  0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
245  0.0 -0.2  0.0  0.0  0.0  0.0  1.500000  0.0  1.0   0.0  ...   -0.1   
246  0.0  1.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
247  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
248  0.0  0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
..   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...    ...   
344  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
345  0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.1   
346  0.0  0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
347  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
348  0.0  0.0  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...   -0.9   

        X_929     X_930  X_931     X_932  X_933      HOUR  DAY_OF_WEEK  \
244 -0.309795 -0.111111    1.0  0.130435    0.0 -0.833333     0.333333   
245 -0.164009  0.111111   -1.0 -1.213043   -0.1 -0.750000     0.000000   
246 -0.120729  0.000000    0.0 -0.347826    0.0 -0.250000    -1.333333   
247 -0.482916  0.000000    0.0 -0.224638    0.0 -0.166667     0.000000   
248  0.669704  1.000000    0.0  0.089855    0.0 -0.416667    -0.333333   
..        ...       ...    ...       ...    ...       ...          ...   
344 -0.517084  0.000000    0.0 -0.763768   -0.1 -0.500000     0.666667   
345 -0.100228  0.111111    0.0 -0.391304    0.0 -0.333333    -1.000000   
346 -0.328018  0.000000    1.0  0.695652    0.1  0.500000    -0.333333   
347 -0.232346 -0.111111    0.0 -0.608696    0.0 -0.166667     0.666667   
348 -0.428246  0.000000    0.0 -0.043478    0.1  0.333333     0.666667   

     Y_Quality  prediction_label  
244   0.529167          0.530003  
245   0.527637          0.531043  
246   0.531414          0.530354  
247   0.531060          0.529611  
248   0.528784          0.530459  
..         ...               ...  
344   0.528506          0.530070  
345   0.525213          0.530684  
346   0.533251          0.530352  
347   0.528094          0.530676  
348   0.532289          0.530253  

[105 rows x 669 columns]

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  X_928  \
244  0.0  0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
245  0.0 -0.2  0.0  0.0  0.0  0.0  1.500000  0.0  1.0   0.0  ...   -0.1   
246  0.0  1.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
247  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
248  0.0  0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
..   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...    ...   
344  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
345  0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.1   
346  0.0  0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
347  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
348  0.0  0.0  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...   -0.9   

        X_929     X_930  X_931     X_932  X_933      HOUR  DAY_OF_WEEK  \
244 -0.309795 -0.111111    1.0  0.130435    0.0 -0.833333     0.333333   
245 -0.164009  0.111111   -1.0 -1.213043   -0.1 -0.750000     0.000000   
246 -0.120729  0.000000    0.0 -0.347826    0.0 -0.250000    -1.333333   
247 -0.482916  0.000000    0.0 -0.224638    0.0 -0.166667     0.000000   
248  0.669704  1.000000    0.0  0.089855    0.0 -0.416667    -0.333333   
..        ...       ...    ...       ...    ...       ...          ...   
344 -0.517084  0.000000    0.0 -0.763768   -0.1 -0.500000     0.666667   
345 -0.100228  0.111111    0.0 -0.391304    0.0 -0.333333    -1.000000   
346 -0.328018  0.000000    1.0  0.695652    0.1  0.500000    -0.333333   
347 -0.232346 -0.111111    0.0 -0.608696    0.0 -0.166667     0.666667   
348 -0.428246  0.000000    0.0 -0.043478    0.1  0.333333     0.666667   

     Y_Quality  prediction_label  
244   0.529167          0.530050  
245   0.527637          0.531033  
246   0.531414          0.530568  
247   0.531060          0.529895  
248   0.528784          0.529345  
..         ...               ...  
344   0.528506          0.529424  
345   0.525213          0.530473  
346   0.533251          0.530075  
347   0.528094          0.530470  
348   0.532289          0.530075  

[105 rows x 669 columns]

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  X_928  \
244  0.0  0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
245  0.0 -0.2  0.0  0.0  0.0  0.0  1.500000  0.0  1.0   0.0  ...   -0.1   
246  0.0  1.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
247  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
248  0.0  0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
..   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...    ...   
344  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
345  0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.1   
346  0.0  0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
347  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
348  0.0  0.0  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...   -0.9   

        X_929     X_930  X_931     X_932  X_933      HOUR  DAY_OF_WEEK  \
244 -0.309795 -0.111111    1.0  0.130435    0.0 -0.833333     0.333333   
245 -0.164009  0.111111   -1.0 -1.213043   -0.1 -0.750000     0.000000   
246 -0.120729  0.000000    0.0 -0.347826    0.0 -0.250000    -1.333333   
247 -0.482916  0.000000    0.0 -0.224638    0.0 -0.166667     0.000000   
248  0.669704  1.000000    0.0  0.089855    0.0 -0.416667    -0.333333   
..        ...       ...    ...       ...    ...       ...          ...   
344 -0.517084  0.000000    0.0 -0.763768   -0.1 -0.500000     0.666667   
345 -0.100228  0.111111    0.0 -0.391304    0.0 -0.333333    -1.000000   
346 -0.328018  0.000000    1.0  0.695652    0.1  0.500000    -0.333333   
347 -0.232346 -0.111111    0.0 -0.608696    0.0 -0.166667     0.666667   
348 -0.428246  0.000000    0.0 -0.043478    0.1  0.333333     0.666667   

     Y_Quality  prediction_label  
244   0.529167          0.529837  
245   0.527637          0.530407  
246   0.531414          0.530629  
247   0.531060          0.529493  
248   0.528784          0.529737  
..         ...               ...  
344   0.528506          0.529812  
345   0.525213          0.530584  
346   0.533251          0.530552  
347   0.528094          0.530624  
348   0.532289          0.530454  

[105 rows x 669 columns]

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  X_928  \
244  0.0  0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
245  0.0 -0.2  0.0  0.0  0.0  0.0  1.500000  0.0  1.0   0.0  ...   -0.1   
246  0.0  1.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
247  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
248  0.0  0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
..   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...    ...   
344  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
345  0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.1   
346  0.0  0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
347  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
348  0.0  0.0  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...   -0.9   

        X_929     X_930  X_931     X_932  X_933      HOUR  DAY_OF_WEEK  \
244 -0.309795 -0.111111    1.0  0.130435    0.0 -0.833333     0.333333   
245 -0.164009  0.111111   -1.0 -1.213043   -0.1 -0.750000     0.000000   
246 -0.120729  0.000000    0.0 -0.347826    0.0 -0.250000    -1.333333   
247 -0.482916  0.000000    0.0 -0.224638    0.0 -0.166667     0.000000   
248  0.669704  1.000000    0.0  0.089855    0.0 -0.416667    -0.333333   
..        ...       ...    ...       ...    ...       ...          ...   
344 -0.517084  0.000000    0.0 -0.763768   -0.1 -0.500000     0.666667   
345 -0.100228  0.111111    0.0 -0.391304    0.0 -0.333333    -1.000000   
346 -0.328018  0.000000    1.0  0.695652    0.1  0.500000    -0.333333   
347 -0.232346 -0.111111    0.0 -0.608696    0.0 -0.166667     0.666667   
348 -0.428246  0.000000    0.0 -0.043478    0.1  0.333333     0.666667   

     Y_Quality  prediction_label  
244   0.529167          0.530954  
245   0.527637          0.530340  
246   0.531414          0.530574  
247   0.531060          0.529747  
248   0.528784          0.529161  
..         ...               ...  
344   0.528506          0.530058  
345   0.525213          0.530693  
346   0.533251          0.530647  
347   0.528094          0.530924  
348   0.532289          0.530652  

[105 rows x 669 columns]

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  X_928  \
244  0.0  0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
245  0.0 -0.2  0.0  0.0  0.0  0.0  1.500000  0.0  1.0   0.0  ...   -0.1   
246  0.0  1.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
247  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
248  0.0  0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
..   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...    ...   
344  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
345  0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.1   
346  0.0  0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
347  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
348  0.0  0.0  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...   -0.9   

        X_929     X_930  X_931     X_932  X_933      HOUR  DAY_OF_WEEK  \
244 -0.309795 -0.111111    1.0  0.130435    0.0 -0.833333     0.333333   
245 -0.164009  0.111111   -1.0 -1.213043   -0.1 -0.750000     0.000000   
246 -0.120729  0.000000    0.0 -0.347826    0.0 -0.250000    -1.333333   
247 -0.482916  0.000000    0.0 -0.224638    0.0 -0.166667     0.000000   
248  0.669704  1.000000    0.0  0.089855    0.0 -0.416667    -0.333333   
..        ...       ...    ...       ...    ...       ...          ...   
344 -0.517084  0.000000    0.0 -0.763768   -0.1 -0.500000     0.666667   
345 -0.100228  0.111111    0.0 -0.391304    0.0 -0.333333    -1.000000   
346 -0.328018  0.000000    1.0  0.695652    0.1  0.500000    -0.333333   
347 -0.232346 -0.111111    0.0 -0.608696    0.0 -0.166667     0.666667   
348 -0.428246  0.000000    0.0 -0.043478    0.1  0.333333     0.666667   

     Y_Quality  prediction_label  
244   0.529167          0.530765  
245   0.527637          0.531402  
246   0.531414          0.531012  
247   0.531060          0.530707  
248   0.528784          0.530591  
..         ...               ...  
344   0.528506          0.531561  
345   0.525213          0.527877  
346   0.533251          0.530214  
347   0.528094          0.531848  
348   0.532289          0.529420  

[105 rows x 669 columns]

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  X_928  \
244  0.0  0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
245  0.0 -0.2  0.0  0.0  0.0  0.0  1.500000  0.0  1.0   0.0  ...   -0.1   
246  0.0  1.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
247  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
248  0.0  0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
..   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...    ...   
344  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
345  0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.1   
346  0.0  0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
347  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
348  0.0  0.0  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...   -0.9   

        X_929     X_930  X_931     X_932  X_933      HOUR  DAY_OF_WEEK  \
244 -0.309795 -0.111111    1.0  0.130435    0.0 -0.833333     0.333333   
245 -0.164009  0.111111   -1.0 -1.213043   -0.1 -0.750000     0.000000   
246 -0.120729  0.000000    0.0 -0.347826    0.0 -0.250000    -1.333333   
247 -0.482916  0.000000    0.0 -0.224638    0.0 -0.166667     0.000000   
248  0.669704  1.000000    0.0  0.089855    0.0 -0.416667    -0.333333   
..        ...       ...    ...       ...    ...       ...          ...   
344 -0.517084  0.000000    0.0 -0.763768   -0.1 -0.500000     0.666667   
345 -0.100228  0.111111    0.0 -0.391304    0.0 -0.333333    -1.000000   
346 -0.328018  0.000000    1.0  0.695652    0.1  0.500000    -0.333333   
347 -0.232346 -0.111111    0.0 -0.608696    0.0 -0.166667     0.666667   
348 -0.428246  0.000000    0.0 -0.043478    0.1  0.333333     0.666667   

     Y_Quality  prediction_label  
244   0.529167          0.530920  
245   0.527637          0.531280  
246   0.531414          0.530450  
247   0.531060          0.529964  
248   0.528784          0.530276  
..         ...               ...  
344   0.528506          0.529964  
345   0.525213          0.530222  
346   0.533251          0.529964  
347   0.528094          0.530222  
348   0.532289          0.530276  

[105 rows x 669 columns]

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  X_928  \
244  0.0  0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
245  0.0 -0.2  0.0  0.0  0.0  0.0  1.500000  0.0  1.0   0.0  ...   -0.1   
246  0.0  1.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
247  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
248  0.0  0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
..   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...    ...   
344  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   -0.9   
345  0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...    0.1   
346  0.0  0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
347  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...    0.0   
348  0.0  0.0  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ...   -0.9   

        X_929     X_930  X_931     X_932  X_933      HOUR  DAY_OF_WEEK  \
244 -0.309795 -0.111111    1.0  0.130435    0.0 -0.833333     0.333333   
245 -0.164009  0.111111   -1.0 -1.213043   -0.1 -0.750000     0.000000   
246 -0.120729  0.000000    0.0 -0.347826    0.0 -0.250000    -1.333333   
247 -0.482916  0.000000    0.0 -0.224638    0.0 -0.166667     0.000000   
248  0.669704  1.000000    0.0  0.089855    0.0 -0.416667    -0.333333   
..        ...       ...    ...       ...    ...       ...          ...   
344 -0.517084  0.000000    0.0 -0.763768   -0.1 -0.500000     0.666667   
345 -0.100228  0.111111    0.0 -0.391304    0.0 -0.333333    -1.000000   
346 -0.328018  0.000000    1.0  0.695652    0.1  0.500000    -0.333333   
347 -0.232346 -0.111111    0.0 -0.608696    0.0 -0.166667     0.666667   
348 -0.428246  0.000000    0.0 -0.043478    0.1  0.333333     0.666667   

     Y_Quality  prediction_label  
244   0.529167          0.529459  
245   0.527637          0.529017  
246   0.531414          0.530067  
247   0.531060          0.527895  
248   0.528784          0.526450  
..         ...               ...  
344   0.528506          0.530966  
345   0.525213          0.532419  
346   0.533251          0.531023  
347   0.528094          0.532374  
348   0.532289          0.528912  

[105 rows x 669 columns]

In [106]:
T10_final_regression_model = finalize_model(T10_model_ada)

In [107]:
T10_prediction = predict_model(T10_final_regression_model, data=T10_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [108]:
T10_datas = T10_prediction['prediction_label']
T10_datas = pd.DataFrame(T10_datas.values, columns = ['Y_Quality'])
T10_datas

Y_Quality
0     0.522168
1     0.522168
2     0.524545
3     0.522613
4     0.529200
..         ...
344   0.535694
345   0.543825
346   0.535694
347   0.534605
348   0.534602

[349 rows x 1 columns]

In [109]:
T10y_idx= T10_class.index
T10y_idx = pd.DataFrame(T10y_idx, columns = ['index'])
T10_datas = pd.concat([T10y_idx, T10_datas], axis = 1)
T10_datas = T10_datas.set_index('index')
T10_datas

Y_Quality
index           
22      0.522168
23      0.522168
85      0.524545
86      0.522613
87      0.529200
...          ...
512     0.535694
516     0.543825
570     0.535694
572     0.534605
578     0.534602

[349 rows x 1 columns]

In [110]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T10_datas, 
                   target=T10_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [111]:
T10_total_models = []

T10_model_rf = create_model('rf', fold = 5)
T10_total_models.append(T10_model_rf)

T10_model_gbc = create_model('gbc', fold = 5)
T10_total_models.append(T10_model_gbc)

T10_model_et = create_model('et', fold = 5)
T10_total_models.append(T10_model_et)

T10_model_catboost = create_model('catboost', fold = 5)
T10_total_models.append(T10_model_catboost)

T10_model_xgb = create_model('xgboost', fold = 5)
T10_total_models.append(T10_model_xgb)

T10_model_ada = create_model('ada', fold = 5)
T10_total_models.append(T10_model_ada)

T10_model_lightgbm = create_model('lightgbm', fold = 5)
T10_total_models.append(T10_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [112]:
T10_model_rf = tune_model(T10_model_rf, fold=5, choose_better = True)

T10_model_gbc = tune_model(T10_model_gbc, fold=5, choose_better = True)

T10_model_et = tune_model(T10_model_et, fold=5, choose_better = True)

T10_model_catboost = tune_model(T10_model_catboost, fold=5, choose_better = True)

T10_model_xgb = tune_model(T10_model_xgb, fold=5, choose_better = True)

T10_model_ada = tune_model(T10_model_ada, fold=5, choose_better = True)

T10_model_lightgbm = tune_model(T10_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [113]:
T10_tuned_models = [T10_model_rf, T10_model_gbc, T10_model_et, T10_model_catboost, T10_model_xgb, T10_model_ada, T10_model_lightgbm]
T10_tuned_models

[RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                        criterion='gini', max_depth=None, max_features='auto',
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.0, min_samples_leaf=1,
                        min_samples_split=2, min_weight_fraction_leaf=0.0,
                        n_estimators=100, n_jobs=-1, oob_score=False,
                        random_state=414, verbose=0, warm_start=False),
 GradientBoostingClassifier(ccp_alpha=0.0, criterion='friedman_mse', init=None,
                            learning_rate=0.05, loss='deviance', max_depth=7,
                            max_features='log2', max_leaf_nodes=None,
                            min_impurity_decrease=0, min_samples_leaf=1,
                            min_samples_split=10, min_weight_fraction_leaf=0.0,
                            n_estimators=60, n_iter_no_change=None,
                            random_state=414, s

In [114]:
for model in T10_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.530065        1                 1               1.0
245   0.530065        1                 1               1.0
246   0.529877        1                 1               1.0
247   0.530065        1                 1               1.0
248   0.522168        0                 0               1.0
..         ...      ...               ...               ...
344   0.529877        1                 1               1.0
345   0.529877        1                 1               1.0
346   0.529200        0                 1               1.0
347   0.530123        1                 1               1.0
348   0.529873        1                 1               1.0

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.530065        1                 1            0.9967
245   0.530065        1                 1            0.9967
246   0.529877        1                 1            0.9967
247   0.530065        1                 1            0.9967
248   0.522168        0                 0            0.9899
..         ...      ...               ...               ...
344   0.529877        1                 1            0.9967
345   0.529877        1                 1            0.9967
346   0.529200        0                 1            0.9967
347   0.530123        1                 1            0.9967
348   0.529873        1                 1            0.9967

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.530065        1                 1            0.4255
245   0.530065        1                 1            0.4255
246   0.529877        1                 1            0.4228
247   0.530065        1                 1            0.4255
248   0.522168        0                 0            0.5105
..         ...      ...               ...               ...
344   0.529877        1                 1            0.4228
345   0.529877        1                 1            0.4228
346   0.529200        0                 1            0.4102
347   0.530123        1                 1            0.4255
348   0.529873        1                 1            0.4228

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.530065        1                 1            0.3338
245   0.530065        1                 1            0.3338
246   0.529877        1                 1            0.3338
247   0.530065        1                 1            0.3338
248   0.522168        0                 0            0.3335
..         ...      ...               ...               ...
344   0.529877        1                 1            0.3338
345   0.529877        1                 1            0.3338
346   0.529200        0                 1            0.3335
347   0.530123        1                 1            0.3338
348   0.529873        1                 1            0.3338

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.530065        1                 1            0.5162
245   0.530065        1                 1            0.5162
246   0.529877        1                 1            0.5162
247   0.530065        1                 1            0.5162
248   0.522168        0                 0            0.4985
..         ...      ...               ...               ...
344   0.529877        1                 1            0.5162
345   0.529877        1                 1            0.5162
346   0.529200        0                 1            0.5071
347   0.530123        1                 1            0.5162
348   0.529873        1                 1            0.5162

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.530065        1                 1            0.9482
245   0.530065        1                 1            0.9482
246   0.529877        1                 1            0.9482
247   0.530065        1                 1            0.9482
248   0.522168        0                 0            0.9995
..         ...      ...               ...               ...
344   0.529877        1                 1            0.9482
345   0.529877        1                 1            0.9482
346   0.529200        0                 1            0.9482
347   0.530123        1                 1            0.9482
348   0.529873        1                 1            0.9482

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.530065        1                 1            0.9998
245   0.530065        1                 1            0.9998
246   0.529877        1                 1            0.9998
247   0.530065        1                 1            0.9998
248   0.522168        0                 0            0.9936
..         ...      ...               ...               ...
344   0.529877        1                 1            0.9998
345   0.529877        1                 1            0.9998
346   0.529200        0                 1            0.7636
347   0.530123        1                 1            0.9998
348   0.529873        1                 1            0.9998

[105 rows x 4 columns]

In [115]:
T10_final_classification_model = finalize_model(T10_model_xgb)

In [116]:
T10_prediction = predict_model(T10_final_classification_model, data=T10_datas)

In [117]:
T10_y_class = pd.DataFrame(T10_class, columns = ['Y_Class'])
T10_idx = T10_y_class.index
T10_y_class = T10_y_class.reset_index()
T10_prediction = pd.concat([T10_prediction, T10_y_class], axis = 1)
T10_prediction = T10_prediction.set_index('index')
T10_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [118]:
T10_prediction

Y_Quality  prediction_label  prediction_score
index                                               
22      0.522168                 0            0.5076
23      0.522168                 0            0.5076
85      0.524545                 0            0.5027
86      0.522613                 0            0.5076
87      0.529200                 1            0.4827
...          ...               ...               ...
512     0.535694                 2            0.5134
516     0.543825                 2            0.5134
570     0.535694                 2            0.5134
572     0.534605                 2            0.5109
578     0.534602                 2            0.5109

[349 rows x 3 columns]

# Test

In [148]:
test_data = pd.read_csv("./test.csv")
test_data

PRODUCT_ID         TIMESTAMP     LINE PRODUCT_CODE  X_1   X_2  X_3   X_4  \
0     TEST_000   2022-09-09 2:01  T100306         T_31  2.0  94.0  0.0  45.0   
1     TEST_001   2022-09-09 2:09  T100304         T_31  2.0  93.0  0.0  45.0   
2     TEST_002   2022-09-09 8:42  T100304         T_31  2.0  95.0  0.0  45.0   
3     TEST_003  2022-09-09 10:56  T010305         A_31  NaN   NaN  NaN   NaN   
4     TEST_004  2022-09-09 11:04  T010306         A_31  NaN   NaN  NaN   NaN   
..         ...               ...      ...          ...  ...   ...  ...   ...   
305   TEST_305  2022-11-05 11:18  T100306         T_31  2.0  91.0  0.0  45.0   
306   TEST_306  2022-11-05 16:39  T100304         T_31  2.0  96.0  0.0  45.0   
307   TEST_307  2022-11-05 16:47  T100306         T_31  2.0  91.0  0.0  45.0   
308   TEST_308  2022-11-05 20:53  T100306         T_31  2.0  95.0  0.0  45.0   
309   TEST_309  2022-11-05 21:01  T100306         T_31  2.0  87.0  0.0  45.0   

      X_5  X_6  ...  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  X_2872  \
0    10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
1    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
2    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
3     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
4     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
..    ...  ...  ...     ...     ...     ...     ...     ...     ...     ...   
305  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
306  11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
307  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
308  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
309  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   

     X_2873  X_2874  X_2875  
0       NaN     NaN     NaN  
1       NaN     NaN     NaN  
2       NaN     NaN     NaN  
3       NaN     NaN     NaN  
4       NaN     NaN     NaN  
..      ...     ...     ...  
305     NaN     NaN     NaN  
306     NaN     NaN     NaN  
307     NaN     NaN     NaN  
308     NaN     NaN     NaN  
309     NaN     NaN     NaN  

[310 rows x 2879 columns]

In [149]:
test_data['YEAR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.year
test_data['MONTH'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.month
test_data['DAY'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day
test_data['HOUR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.hour
test_data['MINUTE'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.minute
test_data['DAY_OF_WEEK'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day_name()

In [150]:
test_data = test_data.drop(['MONTH', 'DAY', 'YEAR', 'MINUTE'], axis = 1)

In [151]:
test_data.drop(colls, inplace = True, axis = 1)

In [152]:
test_data.loc[test_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
test_data.loc[test_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
test_data.loc[test_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
test_data.loc[test_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
test_data.loc[test_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
test_data.loc[test_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
test_data.loc[test_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

test_data.loc[test_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
test_data.loc[test_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
test_data.loc[test_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

test_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
test_data

LINE PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8  ...  \
0    T100306            2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
1    T100304            2  2.0  93.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
2    T100304            2  2.0  95.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
3    T010305            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
4    T010306            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
..       ...          ...  ...   ...  ...   ...   ...  ...   ...   ...  ...   
305  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
306  T100304            2  2.0  96.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
307  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  ...   
308  T100306            2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
309  T100306            2  2.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   

         X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  \
0           NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     2   
1           NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     2   
2           NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     8   
3    444.192308   423.0     NaN     NaN     NaN     NaN     NaN     NaN    10   
4    443.211539   423.0     NaN     NaN     NaN     NaN     NaN     NaN    11   
..          ...     ...     ...     ...     ...     ...     ...     ...   ...   
305         NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    11   
306         NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    16   
307         NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    16   
308         NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    20   
309         NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    21   

     DAY_OF_WEEK  
0              5  
1              5  
2              5  
3              5  
4              5  
..           ...  
305            6  
306            6  
307            6  
308            6  
309            6  

[310 rows x 2797 columns]

In [153]:
TT050304 = test_data[test_data['LINE'] == 'T050304']
TT050307 = test_data[test_data['LINE'] == 'T050307']
TT010305 = test_data[test_data['LINE'] == 'T010305']
TT010306 = test_data[test_data['LINE'] == 'T010306']
TT100304 = test_data[test_data['LINE'] == 'T100304']
TT100306 = test_data[test_data['LINE'] == 'T100306']
TT050304

LINE PRODUCT_CODE  X_1  X_2  X_3  X_4  X_5  X_6  X_7  X_8  ...  \
7   T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
8   T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
14  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
35  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
41  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
42  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
52  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
53  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
54  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
61  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
64  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
65  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
66  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   

        X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  \
7   369.462963   354.0   57.74   52.51   54.45   57.99   63.16     1.0    12   
8   370.259259   353.0   53.18   56.02   41.79   47.94   60.72     1.0    12   
14  369.377359   353.0   49.77   54.93   49.85   48.62   63.18     1.0     6   
35  369.660377   352.0   55.22   58.14   48.93   56.16   64.25     1.0     3   
41  368.018519   352.0   49.67   45.00   49.81   55.19   67.17     1.0    23   
42  368.452830   353.0   51.30   47.66   60.00   53.75   62.58     1.0    23   
52  368.320755   353.0   54.06   51.18   52.17   57.75   63.94     1.0    17   
53  361.226415   342.0   54.04   51.25   54.98   57.22   63.33     1.0    17   
54  367.849057   352.0   55.72   57.57   42.08   55.19   66.06     1.0    18   
61  370.000000   354.0     NaN     NaN     NaN     NaN     NaN     1.0    21   
64  367.943396   352.0     NaN     NaN     NaN     NaN     NaN     1.0     0   
65  368.056604   352.0   51.55   55.55   39.85   47.82   61.59     1.0     3   
66  369.111111   353.0   51.37   55.70   52.49   48.34   62.12     1.0     8   

    DAY_OF_WEEK  
7             6  
8             6  
14            6  
35            7  
41            1  
42            1  
52            3  
53            3  
54            3  
61            7  
64            1  
65            1  
66            1  

[13 rows x 2797 columns]

In [154]:
TT050304.drop(['LINE'], axis = 1, inplace = True)
TT050307.drop(['LINE'], axis = 1, inplace = True)
TT010305.drop(['LINE'], axis = 1, inplace = True)
TT010306.drop(['LINE'], axis = 1, inplace = True)
TT100304.drop(['LINE'], axis = 1, inplace = True)
TT100306.drop(['LINE'], axis = 1, inplace = True)

In [155]:
TT050304.drop(T050304_col, inplace = True, axis = 1)
TT050307.drop(T050307_col, inplace = True, axis = 1)
TT010305.drop(T010305_col, inplace = True, axis = 1)
TT010306.drop(T010306_col, inplace = True, axis = 1)
TT100304.drop(T100304_col, inplace = True, axis = 1)
TT100306.drop(T100306_col, inplace = True, axis = 1)
TT050304

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
7             1  18031.0  18031.0   0.19   0.20   0.19    0.2  354.0  354.0   
8             1  18064.0  18064.0   0.19   0.20   0.19    0.2  355.0  354.0   
14            1    295.0    295.0   0.19   0.21   0.19    0.2   60.0   60.0   
35            1   8632.0   8632.0   0.20   0.21   0.20    0.2  249.0  249.0   
41            1  10712.0  10712.0   0.20   0.21   0.20    0.2  293.0  293.0   
42            1  10729.0  10729.0   0.20   0.21   0.19    0.2  293.0  293.0   
52            1  12261.0  12261.0   0.19   0.21   0.19    0.2  330.0  330.0   
53            1  12283.0  12283.0   0.20   0.21   0.20    0.2  330.0  330.0   
54            1  12305.0  12305.0   0.19   0.21   0.19    0.2  330.0  330.0   
61            1  17990.0  17990.0   0.20   0.21   0.20    0.2  436.0  436.0   
64            1  18026.0  18026.0   0.20   0.21   0.20    0.2  437.0  437.0   
65            1  18220.0  18220.0   0.20   0.21   0.20    0.2  441.0  441.0   
66            1  18514.0  18514.0   0.20   0.21   0.20    0.2  446.0  446.0   

    X_138  ...      X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  X_2870  \
7   354.0  ...  369.462963   354.0   57.74   52.51   54.45   57.99   63.16   
8   355.0  ...  370.259259   353.0   53.18   56.02   41.79   47.94   60.72   
14   60.0  ...  369.377359   353.0   49.77   54.93   49.85   48.62   63.18   
35  249.0  ...  369.660377   352.0   55.22   58.14   48.93   56.16   64.25   
41  293.0  ...  368.018519   352.0   49.67   45.00   49.81   55.19   67.17   
42  293.0  ...  368.452830   353.0   51.30   47.66   60.00   53.75   62.58   
52  330.0  ...  368.320755   353.0   54.06   51.18   52.17   57.75   63.94   
53  330.0  ...  361.226415   342.0   54.04   51.25   54.98   57.22   63.33   
54  330.0  ...  367.849057   352.0   55.72   57.57   42.08   55.19   66.06   
61  436.0  ...  370.000000   354.0     NaN     NaN     NaN     NaN     NaN   
64  437.0  ...  367.943396   352.0     NaN     NaN     NaN     NaN     NaN   
65  441.0  ...  368.056604   352.0   51.55   55.55   39.85   47.82   61.59   
66  446.0  ...  369.111111   353.0   51.37   55.70   52.49   48.34   62.12   

    X_2871  HOUR  DAY_OF_WEEK  
7      1.0    12            6  
8      1.0    12            6  
14     1.0     6            6  
35     1.0     3            7  
41     1.0    23            1  
42     1.0    23            1  
52     1.0    17            3  
53     1.0    17            3  
54     1.0    18            3  
61     1.0    21            7  
64     1.0     0            1  
65     1.0     3            1  
66     1.0     8            1  

[13 rows x 1971 columns]

In [156]:
TT05 = pd.concat([TT050304, TT050307])
TT01 = pd.concat([TT010305, TT010306])
TT10 = pd.concat([TT100304, TT100306])

In [157]:
TT05.drop(T5drop, inplace = True, axis = 1)
TT01.drop(T0drop, inplace = True, axis = 1)
TT10.drop(T1drop, inplace = True, axis = 1)

In [158]:
TT05 = TT05.fillna(TT05.mean())
TT01 = TT01.fillna(TT01.mean())
TT10 = TT10.fillna(TT10.mean())

In [159]:
TT05_idx = TT05['PRODUCT_CODE'].index
TT05_idx = pd.DataFrame(TT05_idx, columns = ['index'])
TT05_idx

index
0       7
1       8
2      14
3      35
4      41
5      42
6      52
7      53
8      54
9      61
10     64
11     65
12     66
13     13
14     36
15     62
16     63
17    130
18    131
19    132
20    248
21    249
22    250
23    251
24    252
25    253
26    254
27    255
28    260
29    263
30    280
31    281
32    282
33    283
34    284
35    285
36    286
37    292
38    293

In [160]:
TT05.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [161]:
TT05c = TT05.columns
TT05scaled = T_05scaler.transform(TT05)
TT05scaled
TT05 = pd.DataFrame(TT05scaled, columns = TT05c)
TT05

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
0    -1.0   -1.0   -1.0    0.0  0.055781  0.053753  0.053999  0.449036   
1    -1.0   -1.0   -1.0    0.0  0.057809  0.053753  0.056037  0.449036   
2    -1.0    0.0   -1.0    0.0 -0.540568 -0.542596 -0.545084 -1.374656   
3     0.0    0.0    0.0    0.0 -0.157201 -0.159229 -0.159959 -0.013774   
4     0.0    0.0    0.0    0.0 -0.067951 -0.069980 -0.070301 -0.134986   
5     0.0    0.0   -1.0    0.0 -0.067951 -0.069980 -0.070301 -0.129477   
6    -1.0    0.0   -1.0    0.0  0.007099  0.005071  0.005094 -0.024793   
7     0.0    0.0    0.0    0.0  0.007099  0.005071  0.005094  0.002755   
8    -1.0    0.0   -1.0    0.0  0.007099  0.005071  0.005094 -0.019284   
9     0.0    0.0    0.0    0.0  0.222110  0.220081  0.221090  0.482094   
10    0.0    0.0    0.0    0.0  0.224138  0.222110  0.223128  0.570248   
11    0.0    0.0    0.0    0.0  0.232252  0.230223  0.231279  0.575758   
12    0.0    0.0    0.0    0.0  0.242394  0.240365  0.241467  0.542700   
13    1.0    1.0    1.0    0.0 -0.195740 -0.197769 -0.196638 -0.151515   
14    1.0    1.0    1.0    0.0 -0.461460 -0.463489 -0.465614 -0.101928   
15    1.0    1.0    1.0    0.0 -0.560852 -0.564909 -0.585838 -0.261708   
16    1.0    1.0    1.0    0.0 -0.556795 -0.560852 -0.583800 -0.157025   
17    1.0    1.0    0.0    0.0  0.197769  0.193712  0.174223  0.129477   
18    1.0    0.0    1.0    0.0  0.197769  0.193712  0.176261  0.057851   
19    1.0    1.0    1.0    0.0  0.201826  0.197769  0.180336  0.046832   
20    1.0    1.0    1.0    0.0  0.822515  0.818458  0.803872  0.669421   
21    1.0    1.0    1.0    0.0  0.822515  0.818458  0.803872  0.630854   
22    1.0    1.0    1.0    0.0  0.824544  0.820487  0.803872  0.586777   
23    1.0    1.0    1.0    0.0  0.824544  0.820487  0.803872  0.592287   
24    1.0    1.0    1.0    0.0  0.824544  0.820487  0.803872  0.581267   
25    1.0    1.0    1.0    0.0  0.824544  0.820487  0.805909  0.586777   
26    1.0    1.0    1.0    0.0  0.832657  0.828600  0.814060  0.608815   
27    1.0    1.0    1.0    0.0  0.834686  0.830629  0.814060  0.619835   
28    1.0    1.0    0.0    0.0  0.834686  0.830629  0.816098  0.680441   
29    0.0    1.0    0.0    0.0  0.840771  0.836714  0.820173  0.752066   
30    1.0    1.0    1.0    0.0  0.938134  0.934077  0.920020  1.033058   
31    1.0    1.0    1.0    0.0  0.940162  0.936105  0.920020  0.955923   
32    1.0    1.0    1.0    0.0  0.960446  0.956389  0.940397  0.900826   
33    1.0    1.0    1.0    0.0  0.960446  0.956389  0.942435  0.884298   
34    1.0    1.0    1.0    0.0  0.972617  0.968560  0.954661  0.884298   
35    1.0    1.0    1.0    0.0  0.972617  0.968560  0.954661  0.895317   
36    1.0    1.0    1.0    0.0  0.974645  0.970588  0.954661  0.895317   
37    1.0    1.0    1.0    0.0  1.003043  0.998986  0.983189  1.000000   
38    1.0    1.0    1.0    0.0  1.003043  0.998986  0.985227  0.994490   

       X_140     X_141  ...    X_2864  X_2865    X_2866    X_2867    X_2868  \
0   0.428571  0.455729  ...  0.739720     2.0  0.695529 -0.472204  0.317934   
1   0.428571  0.460938  ...  1.204775     1.0  0.018217  0.065925 -0.747722   
2  -1.195011 -1.007812  ...  0.689726     1.0 -0.488281 -0.101187 -0.069271   
3  -0.052154  0.158854  ...  0.855015     0.0  0.321225  0.390948 -0.146712   
4  -0.142857  0.184896  ... -0.103867     0.0 -0.503134 -1.623586 -0.072638   
5  -0.138322  0.106771  ...  0.149781     1.0 -0.261025 -1.215773  0.785106   
6  -0.015873 -1.273437  ...  0.072646     1.0  0.148926 -0.676111  0.126015   
7  -0.011338 -0.153646  ... -4.070605   -10.0  0.145956 -0.665379  0.362547   
8  -0.020408  0.184896  ... -0.202836     0.0  0.395492  0.303560 -0.723312   
9   0.437642  0.726563  ...  1.053362     2.0 -0.147179 -0.394826 -0.057115   
10  0.505669  0.690104  ... -0.147740     0.0 -0.147179 -0.394826 -0.057115   
11  0.519274  0.403646  ... -0.081624     0.0 -0.223892 -0.006133 -0.911022   
12  0.487528  0.

In [162]:
TT05 = pd.concat([TT05_idx, TT05], axis = 1)
TT05 = TT05.set_index('index')

In [163]:
TT01_idx = TT01['PRODUCT_CODE'].index
TT01_idx = pd.DataFrame(TT01_idx, columns = ['index'])
TT01_idx

index
0       3
1       6
2      10
3      11
4      38
5      40
6      71
7      86
8      88
9      89
10    116
11    117
12    141
13    142
14      4
15      5
16      9
17     12
18     37
19     39
20     72
21     79
22     87
23    109
24    114
25    115
26    128
27    129

In [164]:
TT01.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [165]:
TT01c = TT01.columns
TT01scaled = T_01scaler.transform(TT01)
TT01 = pd.DataFrame(TT01scaled, columns = TT01c)
TT01

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
0     0.0   0.75 -0.054348    0.0    0.0  0.415730    0.0   -1.0   -1.0   
1     0.0   0.75 -0.054348    0.0    0.0  0.449438    0.0   -1.0   -1.0   
2     0.0   0.00 -0.054348    0.0    0.0  0.516854    0.0   -1.0   -1.0   
3     0.0   1.25 -0.054348    0.0    0.0  0.595506    0.0   -1.0   -1.0   
4     1.0  -0.50 -0.054348    0.0    0.0  1.505618    0.0   -1.0   -1.0   
5     1.0   0.75 -0.054348    0.0    0.0  1.584270    0.0   -1.0   -1.0   
6     1.0  -0.25 -0.054348    0.0    0.0  0.067416    0.0   -1.0   -1.0   
7     0.0  -0.25 -0.054348    0.0    0.0  0.258427    0.0   -1.0   -1.0   
8    16.0   0.00 -0.054348    0.0    0.0  0.258427    0.0   -1.0   -1.0   
9     1.0  -0.25 -0.054348    0.0    0.0  0.258427    0.0   -1.0   -1.0   
10    1.0   0.00 -0.054348    0.0    0.0  0.483146    0.0   -1.0   -1.0   
11    0.0  -0.50 -0.054348    0.0    0.0  0.483146    0.0   -1.0   -1.0   
12    0.0  -0.50 -0.054348    0.0    0.0  0.775281    0.0   -1.0   -1.0   
13    1.0  -0.75 -0.054348    0.0    0.0  0.775281    0.0    0.0   -1.0   
14    1.0   1.25  0.913043    0.0    1.0  0.000000    0.0    0.0    0.0   
15    1.0   0.00  0.945652    0.0    1.0  0.000000    0.0    0.0    0.0   
16    0.0  -0.25  1.010870    0.0    0.0  0.000000    0.0    0.0    0.0   
17    1.0  -0.25  1.086957    0.0    0.0  0.000000    0.0    0.0    0.0   
18    0.0   1.00  0.097826    0.0    1.0  0.000000    0.0    0.0    0.0   
19    1.0   0.25  0.173913    0.0    1.0  0.000000    0.0    0.0    0.0   
20    1.0   1.75  0.902174    0.0    1.0  0.000000    0.0    0.0    0.0   
21    0.0   0.00  0.956522    0.0    1.0  0.000000    0.0    0.0    0.0   
22    0.0   0.50  1.152174    0.0    1.0  0.000000    0.0    0.0    0.0   
23    3.0   1.75  1.326087    0.0    1.0  0.000000    0.0    0.0    0.0   
24    0.0   1.25  1.358696    0.0    1.0  0.000000    0.0    0.0    0.0   
25    1.0   0.75  1.358696    0.0    1.0  0.000000    0.0    0.0    0.0   
26    0.0   1.25  1.500000    0.0    1.0  0.000000    0.0    0.0    0.0   
27    1.0   0.75  1.500000    0.0    1.0  0.000000    0.0    0.0    0.0   

    X_255  ...    X_2858    X_2859    X_2860    X_2861    X_2862  X_2863  \
0     0.0  ... -0.585118 -1.336788  1.159091  1.715374  1.636986     0.2   
1     0.0  ... -1.705924 -2.854922  1.424242  1.957184  1.041096    -0.1   
2     0.0  ... -0.951125 -0.829016  1.204545  1.582338  0.993151     0.1   
3     0.0  ... -1.343554 -1.497409  1.090909  1.374600  1.109589     0.1   
4     0.0  ... -1.920884 -2.207254  0.954545  1.398276  1.383562    -0.3   
5     0.0  ... -1.380046 -1.658031  1.628788  2.220402  1.767123     0.1   
6     0.0  ... -0.420824 -0.549223  1.492424  2.167816  1.863014     0.0   
7     0.0  ...  0.051022 -0.720207  1.492424  2.143966  1.369863     0.1   
8     0.0  ...  5.506263  3.642487  3.325758  3.852278  3.178082     0.1   
9     0.0  ...  0.291414  0.010363  1.446970  2.243647  1.671233     0.0   
10    0.0  ... -1.391573 -2.569948  1.416667  1.918647  1.561644     0.1   
11    0.0  ... -1.849230 -1.870466  1.750000  2.069828  1.993151    -0.9   
12    0.0  ...  2.704854  1.316062  1.727273  2.173563  2.089041     0.1   
13    0.0  ...  3.291153  2.523316  2.484848  2.879659  2.452055     0.1   
14    0.0  ...  0.117716 -0.689119  2.083333  1.851385  1.356164     0.0   
15    0.0  ... -1.153107 -1.388601  1.560606  1.792529  1.493151     0.1   
16    0.0  ... -0.074593  0.113990  1.083333  1.794540  1.684932    -0.9   
17    0.0  ... -1.159318 -1.233161  1.090909  1.678161  1.801370     0.1   
18    0.0  ... -0.302514 -0.854922  1.106061  1.346921  0.883562     0.1   
19    0.0  ... -1.664884 -2.062176  1.825758  2.331897  1.856164     1.0   
20    0.0  ... -0.311680 -1.683938  1.772727  2.225575  1.315068     0.1   
21    0.0  ... -1.083228 -1.735751  1.568182  2.054598  2.157534     0.0   
22    0.0  ...  1.266465 -0.082902  1.833333  2.227299  1.904110     0.1   
23  

In [166]:
TT01 = pd.concat([TT01_idx, TT01], axis = 1)
TT01 = TT01.set_index('index')
TT01

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
index                                                                        
3        0.0   0.75 -0.054348    0.0    0.0  0.415730    0.0   -1.0   -1.0   
6        0.0   0.75 -0.054348    0.0    0.0  0.449438    0.0   -1.0   -1.0   
10       0.0   0.00 -0.054348    0.0    0.0  0.516854    0.0   -1.0   -1.0   
11       0.0   1.25 -0.054348    0.0    0.0  0.595506    0.0   -1.0   -1.0   
38       1.0  -0.50 -0.054348    0.0    0.0  1.505618    0.0   -1.0   -1.0   
40       1.0   0.75 -0.054348    0.0    0.0  1.584270    0.0   -1.0   -1.0   
71       1.0  -0.25 -0.054348    0.0    0.0  0.067416    0.0   -1.0   -1.0   
86       0.0  -0.25 -0.054348    0.0    0.0  0.258427    0.0   -1.0   -1.0   
88      16.0   0.00 -0.054348    0.0    0.0  0.258427    0.0   -1.0   -1.0   
89       1.0  -0.25 -0.054348    0.0    0.0  0.258427    0.0   -1.0   -1.0   
116      1.0   0.00 -0.054348    0.0    0.0  0.483146    0.0   -1.0   -1.0   
117      0.0  -0.50 -0.054348    0.0    0.0  0.483146    0.0   -1.0   -1.0   
141      0.0  -0.50 -0.054348    0.0    0.0  0.775281    0.0   -1.0   -1.0   
142      1.0  -0.75 -0.054348    0.0    0.0  0.775281    0.0    0.0   -1.0   
4        1.0   1.25  0.913043    0.0    1.0  0.000000    0.0    0.0    0.0   
5        1.0   0.00  0.945652    0.0    1.0  0.000000    0.0    0.0    0.0   
9        0.0  -0.25  1.010870    0.0    0.0  0.000000    0.0    0.0    0.0   
12       1.0  -0.25  1.086957    0.0    0.0  0.000000    0.0    0.0    0.0   
37       0.0   1.00  0.097826    0.0    1.0  0.000000    0.0    0.0    0.0   
39       1.0   0.25  0.173913    0.0    1.0  0.000000    0.0    0.0    0.0   
72       1.0   1.75  0.902174    0.0    1.0  0.000000    0.0    0.0    0.0   
79       0.0   0.00  0.956522    0.0    1.0  0.000000    0.0    0.0    0.0   
87       0.0   0.50  1.152174    0.0    1.0  0.000000    0.0    0.0    0.0   
109      3.0   1.75  1.326087    0.0    1.0  0.000000    0.0    0.0    0.0   
114      0.0   1.25  1.358696    0.0    1.0  0.000000    0.0    0.0    0.0   
115      1.0   0.75  1.358696    0.0    1.0  0.000000    0.0    0.0    0.0   
128      0.0   1.25  1.500000    0.0    1.0  0.000000    0.0    0.0    0.0   
129      1.0   0.75  1.500000    0.0    1.0  0.000000    0.0    0.0    0.0   

       X_255  ...    X_2858    X_2859    X_2860    X_2861    X_2862  X_2863  \
index         ...                                                             
3        0.0  ... -0.585118 -1.336788  1.159091  1.715374  1.636986     0.2   
6        0.0  ... -1.705924 -2.854922  1.424242  1.957184  1.041096    -0.1   
10       0.0  ... -0.951125 -0.829016  1.204545  1.582338  0.993151     0.1   
11       0.0  ... -1.343554 -1.497409  1.090909  1.374600  1.109589     0.1   
38       0.0  ... -1.920884 -2.207254  0.954545  1.398276  1.383562    -0.3   
40       0.0  ... -1.380046 -1.658031  1.628788  2.220402  1.767123     0.1   
71       0.0  ... -0.420824 -0.549223  1.492424  2.167816  1.863014     0.0   
86       0.0  ...  0.051022 -0.720207  1.492424  2.143966  1.369863     0.1   
88       0.0  ...  5.506263  3.642487  3.325758  3.852278  3.178082     0.1   
89       0.0  ...  0.291414  0.010363  1.446970  2.243647  1.671233     0.0   
116      0.0  ... -1.391573 -2.569948  1.416667  1.918647  1.561644     0.1   
117      0.0  ... -1.849230 -1.870466  1.750000  2.069828  1.993151    -0.9   
141      0.0  ...  2.704854  1.316062  1.727273  2.173563  2.089041     0.1   
142      0.0  ...  3.291153  2.523316  2.484848  2.879659  2.452055     0.1   
4        0.0  ...  0.117716 -0.689119  2.083333  1.851385  1.356164     0.0   
5        0.0  ... -1.153107 -1.388601  1.560606  1.792529  1.493151     0.1   
9        0.0  ... -0.074593  0.113990  1.083333  1.794540  1.684932    -0.9   
12       0.0  ... -1.159318 -1.233161  1.090909  1.678161  1.801370     0.1   
37       0.0  ... -0.302514 -0.854922  1.106061  1.346921  0.883562     0.1   
39     

In [167]:
TT10_idx = TT10['PRODUCT_CODE'].index
TT10_idx = pd.DataFrame(TT10_idx, columns = ['index'])
TT10_idx

index
0        1
1        2
2       15
3       17
4       20
..     ...
238    301
239    305
240    307
241    308
242    309

[243 rows x 1 columns]

In [169]:
TT10.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [170]:
TT10c = TT10.columns
TT10scaled = T_10scaler.transform(TT10)
TT10 = pd.DataFrame(TT10scaled, columns = TT10c)
TT10

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...     X_926  \
0    0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -1.747121   
1    0.0  0.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  1.458253   
2    0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  2.507198   
3    0.0  0.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  3.604127   
4    0.0 -0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  3.331574   
..   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...       ...   
238  0.0 -0.2  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ... -0.872841   
239  0.0 -0.8  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ... -0.535029   
240  0.0 -0.8  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ... -0.934261   
241  0.0  0.0  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ... -0.290563   
242  0.0 -1.6  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ... -0.487044   

     X_927  X_928     X_929     X_930  X_931     X_932  X_933      HOUR  \
0    -1.24    0.1  0.788155  1.000000    0.0  0.086956    0.0 -0.666667   
1     1.90    0.0  0.002278  0.000000    0.0 -0.391304    0.0 -0.166667   
2     1.00   -0.9 -0.357631  0.000000    0.0 -0.173913    0.0 -0.416667   
3     1.00    0.0  0.478360  0.000000    1.0  0.043478    0.0  1.083333   
4     2.30   -0.9 -0.307517  0.000000    0.0  0.044927    0.0 -0.750000   
..     ...    ...       ...       ...    ...       ...    ...       ...   
238   0.18    0.1  0.806378  1.000000    0.0 -0.260870    0.0  0.416667   
239  -0.94    0.0  0.847380  0.555556    0.0 -0.782609    0.0  0.083333   
240  -0.52   -0.3 -0.236902  0.000000    0.0 -0.521739    0.0  0.500000   
241  -1.14    0.0  0.088838  0.111111    0.0 -0.869565    0.0  0.833333   
242  -0.10    0.1  0.232346  0.000000    0.0 -0.763768    0.0  0.916667   

     DAY_OF_WEEK  
0       0.000000  
1       0.000000  
2      -1.000000  
3      -0.333333  
4       0.000000  
..           ...  
238     0.000000  
239     0.333333  
240     0.333333  
241     0.333333  
242     0.333333  

[243 rows x 667 columns]

In [171]:
TT10 = pd.concat([TT10_idx, TT10], axis = 1)
TT10 = TT10.set_index('index')
TT10

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...     X_926  \
index                                                          ...             
1      0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -1.747121   
2      0.0  0.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  1.458253   
15     0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  2.507198   
17     0.0  0.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  3.604127   
20     0.0 -0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...  3.331574   
...    ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...       ...   
301    0.0 -0.2  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ... -0.872841   
305    0.0 -0.8  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ... -0.535029   
307    0.0 -0.8  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ... -0.934261   
308    0.0  0.0  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ... -0.290563   
309    0.0 -1.6  0.0  0.0  0.0  0.0  1.000000  0.0  1.0   0.0  ... -0.487044   

       X_927  X_928     X_929     X_930  X_931     X_932  X_933      HOUR  \
index                                                                       
1      -1.24    0.1  0.788155  1.000000    0.0  0.086956    0.0 -0.666667   
2       1.90    0.0  0.002278  0.000000    0.0 -0.391304    0.0 -0.166667   
15      1.00   -0.9 -0.357631  0.000000    0.0 -0.173913    0.0 -0.416667   
17      1.00    0.0  0.478360  0.000000    1.0  0.043478    0.0  1.083333   
20      2.30   -0.9 -0.307517  0.000000    0.0  0.044927    0.0 -0.750000   
...      ...    ...       ...       ...    ...       ...    ...       ...   
301     0.18    0.1  0.806378  1.000000    0.0 -0.260870    0.0  0.416667   
305    -0.94    0.0  0.847380  0.555556    0.0 -0.782609    0.0  0.083333   
307    -0.52   -0.3 -0.236902  0.000000    0.0 -0.521739    0.0  0.500000   
308    -1.14    0.0  0.088838  0.111111    0.0 -0.869565    0.0  0.833333   
309    -0.10    0.1  0.232346  0.000000    0.0 -0.763768    0.0  0.916667   

       DAY_OF_WEEK  
index               
1         0.000000  
2         0.000000  
15       -1.000000  
17       -0.333333  
20        0.000000  
...            ...  
301       0.000000  
305       0.333333  
307       0.333333  
308       0.333333  
309       0.333333  

[243 rows x 667 columns]

In [172]:
from pycaret.regression import *
TT05_prediction = predict_model(T05_final_regression_model, data=TT05)
TT01_prediction = predict_model(T01_final_regression_model, data=TT01)
TT10_prediction = predict_model(T10_final_regression_model, data=TT10)

In [173]:
TT05_prediction = pd.DataFrame(TT05_prediction, columns = ['prediction_label'])
TT01_prediction = pd.DataFrame(TT01_prediction, columns = ['prediction_label'])
TT10_prediction = pd.DataFrame(TT10_prediction, columns = ['prediction_label'])
TT05_prediction

prediction_label
0           0.530225
1           0.530034
2           0.530684
3           0.530882
4           0.531583
5           0.529969
6           0.530693
7           0.530657
8           0.531362
9           0.531627
10          0.532225
11          0.531649
12          0.531615
13          0.531814
14          0.530738
15          0.531369
16          0.532561
17          0.530560
18          0.530512
19          0.530203
20          0.533248
21          0.531873
22          0.530999
23          0.531048
24          0.531052
25          0.531718
26          0.531799
27          0.532200
28          0.535032
29          0.534040
30          0.532945
31          0.533005
32          0.530596
33          0.531592
34          0.533967
35          0.533074
36          0.533393
37          0.532273
38          0.532538

In [174]:
TT05_y_class = pd.DataFrame(TT05, columns = ['PRODUCT_CODE'])
TT05_idx = TT05_y_class.index
TT05_y_class = TT05_y_class.reset_index()
TT05_prediction = pd.concat([TT05_prediction, TT05_y_class], axis = 1)
TT05_prediction = TT05_prediction.set_index('index')
TT05_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)
TT05_prediction

prediction_label
index                  
7              0.530225
8              0.530034
14             0.530684
35             0.530882
41             0.531583
42             0.529969
52             0.530693
53             0.530657
54             0.531362
61             0.531627
64             0.532225
65             0.531649
66             0.531615
13             0.531814
36             0.530738
62             0.531369
63             0.532561
130            0.530560
131            0.530512
132            0.530203
248            0.533248
249            0.531873
250            0.530999
251            0.531048
252            0.531052
253            0.531718
254            0.531799
255            0.532200
260            0.535032
263            0.534040
280            0.532945
281            0.533005
282            0.530596
283            0.531592
284            0.533967
285            0.533074
286            0.533393
292            0.532273
293            0.532538

In [175]:
TT01_y_class = pd.DataFrame(TT01, columns = ['PRODUCT_CODE'])
TT01_idx = TT01_y_class.index
TT01_y_class = TT01_y_class.reset_index()
TT01_prediction = pd.concat([TT01_prediction, TT01_y_class], axis = 1)
TT01_prediction = TT01_prediction.set_index('index')
TT01_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [176]:
TT10_y_class = pd.DataFrame(TT10, columns = ['PRODUCT_CODE'])
TT10_idx = TT10_y_class.index
TT10_y_class = TT10_y_class.reset_index()
TT10_prediction = pd.concat([TT10_prediction, TT10_y_class], axis = 1)
TT10_prediction = TT10_prediction.set_index('index')
TT10_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [179]:
TT05_datas = TT05_prediction['prediction_label']
TT05_datas = pd.DataFrame(TT05_datas.values, columns = ['Y_Quality'])
TT05_datas

Y_Quality
0    0.530225
1    0.530034
2    0.530684
3    0.530882
4    0.531583
5    0.529969
6    0.530693
7    0.530657
8    0.531362
9    0.531627
10   0.532225
11   0.531649
12   0.531615
13   0.531814
14   0.530738
15   0.531369
16   0.532561
17   0.530560
18   0.530512
19   0.530203
20   0.533248
21   0.531873
22   0.530999
23   0.531048
24   0.531052
25   0.531718
26   0.531799
27   0.532200
28   0.535032
29   0.534040
30   0.532945
31   0.533005
32   0.530596
33   0.531592
34   0.533967
35   0.533074
36   0.533393
37   0.532273
38   0.532538

In [180]:
TT05y_idx= TT05_prediction.index
TT05y_idx = pd.DataFrame(TT05y_idx, columns = ['index'])
TT05_datas = pd.concat([TT05y_idx, TT05_datas], axis = 1)
TT05_datas = TT05_datas.set_index('index')
TT05_datas

Y_Quality
index           
7       0.530225
8       0.530034
14      0.530684
35      0.530882
41      0.531583
42      0.529969
52      0.530693
53      0.530657
54      0.531362
61      0.531627
64      0.532225
65      0.531649
66      0.531615
13      0.531814
36      0.530738
62      0.531369
63      0.532561
130     0.530560
131     0.530512
132     0.530203
248     0.533248
249     0.531873
250     0.530999
251     0.531048
252     0.531052
253     0.531718
254     0.531799
255     0.532200
260     0.535032
263     0.534040
280     0.532945
281     0.533005
282     0.530596
283     0.531592
284     0.533967
285     0.533074
286     0.533393
292     0.532273
293     0.532538

In [181]:
TT01_datas = TT01_prediction['prediction_label']
TT01_datas = pd.DataFrame(TT01_datas.values, columns = ['Y_Quality'])
TT01_datas

Y_Quality
0    0.528898
1    0.530192
2    0.530381
3    0.531015
4    0.535995
5    0.531552
6    0.528291
7    0.527548
8    0.527854
9    0.529275
10   0.529721
11   0.529890
12   0.530010
13   0.529968
14   0.530724
15   0.530649
16   0.530060
17   0.531247
18   0.527800
19   0.529264
20   0.530256
21   0.530429
22   0.530886
23   0.529800
24   0.530995
25   0.530805
26   0.530217
27   0.530946

In [182]:
TT01y_idx= TT01_prediction.index
TT01y_idx = pd.DataFrame(TT01y_idx, columns = ['index'])
TT01_datas = pd.concat([TT01y_idx, TT01_datas], axis = 1)
TT01_datas = TT01_datas.set_index('index')
TT01_datas

Y_Quality
index           
3       0.528898
6       0.530192
10      0.530381
11      0.531015
38      0.535995
40      0.531552
71      0.528291
86      0.527548
88      0.527854
89      0.529275
116     0.529721
117     0.529890
141     0.530010
142     0.529968
4       0.530724
5       0.530649
9       0.530060
12      0.531247
37      0.527800
39      0.529264
72      0.530256
79      0.530429
87      0.530886
109     0.529800
114     0.530995
115     0.530805
128     0.530217
129     0.530946

In [183]:
TT10_datas = TT10_prediction['prediction_label']
TT10_datas = pd.DataFrame(TT10_datas.values, columns = ['Y_Quality'])
TT10_datas

Y_Quality
0     0.530332
1     0.530272
2     0.529873
3     0.530065
4     0.529873
..         ...
238   0.530176
239   0.529877
240   0.530065
241   0.530065
242   0.530242

[243 rows x 1 columns]

In [184]:
TT10y_idx= TT10_prediction.index
TT10y_idx = pd.DataFrame(TT10y_idx, columns = ['index'])
TT10_datas = pd.concat([TT10y_idx, TT10_datas], axis = 1)
TT10_datas = TT10_datas.set_index('index')
TT10_datas

Y_Quality
index           
1       0.530332
2       0.530272
15      0.529873
17      0.530065
20      0.529873
...          ...
301     0.530176
305     0.529877
307     0.530065
308     0.530065
309     0.530242

[243 rows x 1 columns]

In [185]:
from pycaret.classification import *

In [186]:
TT05_predictions = predict_model(T05_final_classification_model, data=TT05_datas)
TT01_predictions = predict_model(T01_final_classification_model, data=TT01_datas)
TT10_predictions = predict_model(T10_final_classification_model, data=TT10_datas)

In [187]:
TT05_predictions = pd.DataFrame(TT05_predictions, columns = ['prediction_label'])
TT01_predictions = pd.DataFrame(TT01_predictions, columns = ['prediction_label'])
TT10_predictions = pd.DataFrame(TT10_predictions, columns = ['prediction_label'])

In [188]:
TT05_idxf = TT05_datas.index
TT05_p = pd.DataFrame(TT05_idxf, columns = ['index'])
TT05_predictions = pd.concat([TT05_p, TT05_predictions], axis = 1)
TT05_predictions = TT05_predictions.set_index('index')
TT05_predictions

prediction_label
index                  
7                     1
8                     1
14                    1
35                    1
41                    1
42                    1
52                    1
53                    1
54                    1
61                    1
64                    1
65                    1
66                    1
13                    1
36                    1
62                    1
63                    1
130                   1
131                   1
132                   1
248                   1
249                   1
250                   1
251                   1
252                   1
253                   1
254                   1
255                   1
260                   1
263                   1
280                   1
281                   1
282                   1
283                   1
284                   1
285                   1
286                   1
292                   1
293                   1

In [189]:
TT01_idxf = TT01_datas.index
TT01_p = pd.DataFrame(TT01_idxf, columns = ['index'])
TT01_predictions = pd.concat([TT01_p, TT01_predictions], axis = 1)
TT01_predictions = TT01_predictions.set_index('index')
TT01_predictions

prediction_label
index                  
3                     1
6                     1
10                    1
11                    1
38                    2
40                    1
71                    1
86                    1
88                    1
89                    1
116                   1
117                   1
141                   1
142                   1
4                     1
5                     1
9                     1
12                    1
37                    1
39                    1
72                    1
79                    1
87                    1
109                   1
114                   1
115                   1
128                   1
129                   1

In [190]:
TT10_idxf = TT10_datas.index
TT10_p = pd.DataFrame(TT10_idxf, columns = ['index'])
TT10_predictions = pd.concat([TT10_p, TT10_predictions], axis = 1)
TT10_predictions = TT10_predictions.set_index('index')
TT10_predictions

prediction_label
index                  
1                     1
2                     1
15                    1
17                    1
20                    1
...                 ...
301                   1
305                   1
307                   1
308                   1
309                   1

[243 rows x 1 columns]

In [191]:
final_test = pd.concat([TT05_predictions, TT01_predictions, TT10_predictions])
final_test

prediction_label
index                  
7                     1
8                     1
14                    1
35                    1
41                    1
...                 ...
301                   1
305                   1
307                   1
308                   1
309                   1

[310 rows x 1 columns]

In [192]:
final_test = final_test.sort_index(ascending=True)
final_test['prediction_label']

index
0      1
1      1
2      1
3      1
4      1
      ..
305    1
306    1
307    1
308    1
309    1
Name: prediction_label, Length: 310, dtype: int32

In [193]:
#52
sample_submission = pd.read_csv('sample_submission.csv')
sample_submission['Y_Class'] = final_test['prediction_label']
display(sample_submission.head())
sample_submission.to_csv('line3_otherdrop_robust_regpyc_classpyc_fillclassmean_submission.csv',index=False)

PRODUCT_ID  Y_Class
0   TEST_000        1
1   TEST_001        1
2   TEST_002        1
3   TEST_003        1
4   TEST_004        1

In [194]:
final_test['prediction_label'].value_counts()

1    309
2      1
Name: prediction_label, dtype: int64

In [195]:
np.array(final_test['prediction_label'])

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,